# CAPSTONE PROJECT THE BATTEL OF NEIGHBORHOODS

Applied Data Science Capstone Assignment

By. Leonardo Vega, MSc.

---

##  GEOREFERENCED REAL STATE MARKET STUDY - SUPIA, CALDAS, COLOMBIA

### Business Understanding

The definition of a type of real state project is required in a piece of land nearby Supia Town Center, Caldas, Colombia.  The Land owner (as developer) wants to perform a **georeferenced real state market** study that provide some insights to support the decision of which type project start to plan.

geopy Nominatim is used for Geocoding purposes.  Then a foursquuare API is used to explore a **Region of Interest** and understand venue offer.  

The study has the following scope:

1. **Environmental analysis (sociogemographics)** :  National sociodemographics georeferenced analysis; in this section the variables **annual population variation**, **annual household variation**, and the **ratio household / housing units** is evaluated.
2. **Environmental analysis (economic construction sector)** :  National construction sector  georeferenced analysis; in this section the variables **annual ICCV (Construction Cost Index Variation) variation**, **annual IPC (Consumer Price Index) variation**, and **annual IPV (Sales Price Index) variation** is evaluated.
3. **Market analysis**:  National real-state market georeferenced analysis; in this section the variables **annual sales variation**, **annual new home launches projects variation**, and **annual offer housing variation** is evaluated.
4. **Region of Interest analysis**: After conclusions national scope analysis, an analysis of a Region of Interest is performed to get further insight of what sort of project start to plan.  This region is chosen based on its proximity and cultual and economical influence to Supía.
- Región of interest
> - Supía
> - Riosucio
> - Marmato
> - Manizales
> - Pereira
> - Medellín
5. **Places of Interest Analysis**: a real state market will continue by georeferencing places of interest in supía, with its  own set of data, as shown below.  Finally a map evaluation (distance from GPS certified point in land) to different places is performed.

| `Places of Interest`            | `Data Source`                         | `Data of Interest`                                                |
| :---                            | :---                                  | :---                                                              |
| Project location                | Topograghy Study                      | Coordinates                                                       |
| Neighborhoods of Supía          | Supía Development Plan                | Coordinates                                                       |
| Educational Institutions        | Supía Development Plan                | Coordinates                                                       |
| Health Services Entities        | Supía Development Plan                | Coordinates                                                       |
| Current Real State Offer        | Real-State Market Study               | Coordinates, Type, Avaliable Offer, Rooms, Social Level, Price/m2 |
| Venue offer 2                   | Foursquare                            | Coordinates, venue, venue category                                |

Finally a map evaluation (distance from GPS certified point in land) to different places is performed.

### Download and Explore Dataset

In [1]:
#pip install scikit-learn

In [2]:
# Importing Libraries

import requests # Library to handle requests
import os # Find current working directory

import numpy as np # library to handle data in a vectorized manner
import pandas as pd # library for data analsysis
import sklearn
from sklearn.linear_model import LinearRegression
lm=LinearRegression()

#!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values
from functools import partial # To pass extra options to the geocode
from geopy.extra.rate_limiter import RateLimiter # RateLimiter allows to perform bulk operations while gracefully handling error responses and adding delays when needed.
from geopy import distance

# Partial geopy parameter definition
geolocator = Nominatim(user_agent="default_user_agent")
geocode = partial(geolocator.geocode, language="es")

#! pip install folium==0.5.0
import folium # plotting library

print('Libraries imported')

ImportError: Can't determine version for numexpr

---

### 1. Environmental Analysis (Sociodemographics)
#### 1a. Download and Explore Dataset Census

**Downloading the latest census 2018** from the national statistics department, DANE.

In [ ]:
# Read data from CSV file
os.listdir(os.getcwd())
df_censo2018 = pd.read_csv('censo2018.csv', encoding = 'latin-1')
df_censo2018 = df_censo2018.rename(columns={"Department":"Department-2018","Municipality":"Municipality-2018"})

print('The censo has {} municipalities.'.format(len(df_censo2018),df_censo2018.shape[0]))
df_censo2018.head()

The censo has 1122 municipalities.


Department-2018 Municipality-2018  Total 2018  Housing units 2018  \
0       Antioquia          Medellín     2427129              892151   
1       Antioquia         Abejorral       20367                8511   
2       Antioquia          Abriaquí        2695                1056   
3       Antioquia        Alejandría        4657                2155   
4       Antioquia             Amagá       30227               11638   

   Households 2018  People 2018  
0           815493      2372330  
1             6028        17599  
2              776         2159  
3             1384         3839  
4             8884        26821

In [ ]:
df = df_censo2018['Department-2018']
df.unique()

array(['Antioquia', 'Atlántico', 'Bogotá, D.C.', 'Bolívar', 'Boyacá',
       'Caldas', 'Caquetá', 'Cauca', 'Cesar', 'Córdoba', 'Cundinamarca',
       'Chocó', 'Huila', 'La Guajira', 'Magdalena', 'Meta', 'Nariño',
       'Norte de Santander', 'Quindío', 'Risaralda', 'Santander', 'Sucre',
       'Tolima', 'Valle del Cauca', 'Arauca', 'Casanare', 'Putumayo',
       'Archipiélago de San Andrés', 'Amazonas', 'Guainía', 'Guaviare',
       'Vaupés', 'Vichada'], dtype=object)

Validating if there are duplicated municipalities in censo 2018

In [ ]:
mun=df_censo2018['Municipality-2018']+', '+df_censo2018['Department-2018']
mun_2018 = pd.DataFrame(mun, columns=['Municipality-2018'])
print('The censo has {} municipalities.'.format(mun_2018['Municipality-2018'].nunique(),df_censo2018.shape[0]))

The censo has 1122 municipalities.


In [ ]:
df_censo2018.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1122 entries, 0 to 1121
Data columns (total 6 columns):
 #   Column              Non-Null Count  Dtype 
---  ------              --------------  ----- 
 0   Department-2018     1122 non-null   object
 1   Municipality-2018   1122 non-null   object
 2   Total 2018          1122 non-null   int64 
 3   Housing units 2018  1122 non-null   int64 
 4   Households 2018     1122 non-null   int64 
 5   People 2018         1122 non-null   int64 
dtypes: int64(4), object(2)
memory usage: 52.7+ KB


In [ ]:
df_censo2018[['Location']] = mun_2018[['Municipality-2018']]
df_censo2018.head()

Department-2018 Municipality-2018  Total 2018  Housing units 2018  \
0       Antioquia          Medellín     2427129              892151   
1       Antioquia         Abejorral       20367                8511   
2       Antioquia          Abriaquí        2695                1056   
3       Antioquia        Alejandría        4657                2155   
4       Antioquia             Amagá       30227               11638   

   Households 2018  People 2018               Location  
0           815493      2372330    Medellín, Antioquia  
1             6028        17599   Abejorral, Antioquia  
2              776         2159    Abriaquí, Antioquia  
3             1384         3839  Alejandría, Antioquia  
4             8884        26821       Amagá, Antioquia

It is demonstrated there are not duplicated municipalities in census 2018. Accordingly to the latest census, Colombia has 1,222 municipalities

Downloading census 2005 from the national statistics department, DANE.

In [ ]:
# Read data from CSV file
os.listdir(os.getcwd())
df_censo2005 = pd.read_csv('censo2005.csv', encoding = 'latin-1')
df_censo2005 = df_censo2005.rename(columns={"Department":"Department-2005","Municipality":"Municipality-2005"})

print('The censo has {} municipalities.'.format(len(df_censo2005),df_censo2005.shape[0]))
df_censo2005.head() 

The censo has 1114 municipalities.


Department-2005 Municipality-2005  Total 2005  Households 2005
0       Antioquia          Medellín     2219861         605192.0
1       Antioquia         Abejorral       19893           5064.0
2       Antioquia          Abriaquí        2173            579.0
3       Antioquia        Alejandría        3730           1045.0
4       Antioquia             Amagá       27115           6928.0

In [ ]:
df = df_censo2005['Department-2005']
df.unique()

array(['Antioquia', 'Atlántico', 'Bogotá, D.C.', 'Bolívar', 'Boyacá',
       'Caldas', 'Caquetá', 'Cauca', 'Cesar', 'Córdoba', 'Cundinamarca',
       'Chocó', 'Huila', 'La Guajira', 'Magdalena', 'Meta', 'Nariño',
       'Norte de Santander', 'Quindío', 'Risaralda', 'Santander', 'Sucre',
       'Tolima', 'Valle del Cauca', 'Arauca', 'Casanare', 'Putumayo',
       'Archipiélago de San Andrés', 'Amazonas', 'Guainía', 'Guaviare',
       'Vaupés', 'Vichada'], dtype=object)

Validating if there are duplicated municipalities in censo 2005

In [ ]:
mun=df_censo2005['Municipality-2005']+', '+df_censo2005['Department-2005']
mun_2005= pd.DataFrame(mun, columns=['Municipality-2005'])
print('The censo has {} municipalities.'.format(mun_2005['Municipality-2005'].nunique(),df_censo2005.shape[0]))

The censo has 1114 municipalities.


In [ ]:
df_censo2005.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1114 entries, 0 to 1113
Data columns (total 4 columns):
 #   Column             Non-Null Count  Dtype  
---  ------             --------------  -----  
 0   Department-2005    1114 non-null   object 
 1   Municipality-2005  1114 non-null   object 
 2   Total 2005         1114 non-null   int64  
 3   Households 2005    1094 non-null   float64
dtypes: float64(1), int64(1), object(2)
memory usage: 34.9+ KB


In [ ]:
df_censo2005[['Location']] = mun_2005[['Municipality-2005']]
df_censo2005.head()

Department-2005 Municipality-2005  Total 2005  Households 2005  \
0       Antioquia          Medellín     2219861         605192.0   
1       Antioquia         Abejorral       19893           5064.0   
2       Antioquia          Abriaquí        2173            579.0   
3       Antioquia        Alejandría        3730           1045.0   
4       Antioquia             Amagá       27115           6928.0   

                Location  
0    Medellín, Antioquia  
1   Abejorral, Antioquia  
2    Abriaquí, Antioquia  
3  Alejandría, Antioquia  
4       Amagá, Antioquia

It is demonstrated there are not duplicated municipalities in census 2005. Accordingly to the census 2005, Colombia had 1,114 municipalities at that time

Updating index to df_censo2018 to location

In [ ]:
#update censo 2018 index to be municipality
if(df_censo2018.index.name != 'Location'):
    df_censo2018 = df_censo2018.set_index('Location')

df_censo2018.head()

Department-2018 Municipality-2018  Total 2018  \
Location                                                              
Medellín, Antioquia         Antioquia          Medellín     2427129   
Abejorral, Antioquia        Antioquia         Abejorral       20367   
Abriaquí, Antioquia         Antioquia          Abriaquí        2695   
Alejandría, Antioquia       Antioquia        Alejandría        4657   
Amagá, Antioquia            Antioquia             Amagá       30227   

                       Housing units 2018  Households 2018  People 2018  
Location                                                                 
Medellín, Antioquia                892151           815493      2372330  
Abejorral, Antioquia                 8511             6028        17599  
Abriaquí, Antioquia                  1056              776         2159  
Alejandría, Antioquia                2155             1384         3839  
Amagá, Antioquia                    11638             8884        26821

Updating index to df_censo2005 to location

In [ ]:
#update censo 2005 index to be municipality
if(df_censo2005.index.name != 'Location'):
    df_censo2005 = df_censo2005.set_index('Location')

df_censo2005.head()

Department-2005 Municipality-2005  Total 2005  \
Location                                                              
Medellín, Antioquia         Antioquia          Medellín     2219861   
Abejorral, Antioquia        Antioquia         Abejorral       19893   
Abriaquí, Antioquia         Antioquia          Abriaquí        2173   
Alejandría, Antioquia       Antioquia        Alejandría        3730   
Amagá, Antioquia            Antioquia             Amagá       27115   

                       Households 2005  
Location                                
Medellín, Antioquia           605192.0  
Abejorral, Antioquia            5064.0  
Abriaquí, Antioquia              579.0  
Alejandría, Antioquia           1045.0  
Amagá, Antioquia                6928.0

Comparing Census municipalities, and mantining municipalities with data available from both census

In [ ]:
frames = [df_censo2018, df_censo2005]
census = pd.concat(frames, axis=1, join='inner')
census

Department-2018 Municipality-2018  Total 2018  \
Location                                                                
Medellín, Antioquia           Antioquia          Medellín     2427129   
Abejorral, Antioquia          Antioquia         Abejorral       20367   
Abriaquí, Antioquia           Antioquia          Abriaquí        2695   
Alejandría, Antioquia         Antioquia        Alejandría        4657   
Amagá, Antioquia              Antioquia             Amagá       30227   
...                                 ...               ...         ...   
Taraira, Vaupés                  Vaupés           Taraira        2215   
Puerto Carreño, Vichada         Vichada    Puerto Carreño       20936   
La Primavera, Vichada           Vichada      La Primavera       10122   
Santa Rosalía, Vichada          Vichada     Santa Rosalía        4059   
Cumaribo, Vichada               Vichada          Cumaribo       72691   

                         Housing units 2018  Households 2018  People 2018  \
Location                                                                    
Medellín, Antioquia                  892151           815493      2372330   
Abejorral, Antioquia                   8511             6028        17599   
Abriaquí, Antioquia                    1056              776         2159   
Alejandría, Antioquia                  2155             1384         3839   
Amagá, Antioquia                      11638             8884        26821   
...                                     ...              ...          ...   
Taraira, Vaupés                         402              411         2010   
Puerto Carreño, Vichada                6866             5816        19788   
La Primavera, Vichada                  3326             2739         9690   
Santa Rosalía, Vichada                 1130             1074         4026   
Cumaribo, Vichada                      9476             9533        43138   

                        Department-2005 Municipality-2005  Total 2005  \
Location                                                                
Medellín, Antioquia           Antioquia          Medellín     2219861   
Abejorral, Antioquia          Antioquia         Abejorral       19893   
Abriaquí, Antioquia           Antioquia          Abriaquí        2173   
Alejandría, Antioquia         Antioquia        Alejandría        3730   
Amagá, Antioquia              Antioquia             Amagá       27115   
...                                 ...               ...         ...   
Taraira, Vaupés                  Vaupés           Taraira        1015   
Puerto Carreño, Vichada         Vichada    Puerto Carreño       12897   
La Primavera, Vichada           Vichada      La Primavera        4517   
Santa Rosalía, Vichada          Vichada     Santa Rosalía        3188   
Cumaribo, Vichada               Vichada          Cumaribo       23990   

                         Households 2005  
Location                                  
Medellín, Antioquia             605192.0  
Abejorral, Antioquia              5064.0  
Abriaquí, Antioquia                579.0  
Alejandría, Antioquia             1045.0  
Amagá, Antioquia                  6928.0  
...                                  ...  
Taraira, Vaupés                    226.0  
Puerto Carreño, Vichada           2804.0  
La Primavera, Vichada                NaN  
Santa Rosalía, Vichada             584.0  
Cumaribo, Vichada                 4967.0  

[1095 rows x 10 columns]

Drop municipalities with missing information

In [ ]:
# Remove muncipalities that are missing information
census.dropna(inplace=True)

In [ ]:
census.astype({'Households 2005':'int64'}).dtypes
census.info()

<class 'pandas.core.frame.DataFrame'>
Index: 1085 entries, Medellín, Antioquia to Cumaribo, Vichada
Data columns (total 10 columns):
 #   Column              Non-Null Count  Dtype  
---  ------              --------------  -----  
 0   Department-2018     1085 non-null   object 
 1   Municipality-2018   1085 non-null   object 
 2   Total 2018          1085 non-null   int64  
 3   Housing units 2018  1085 non-null   int64  
 4   Households 2018     1085 non-null   int64  
 5   People 2018         1085 non-null   int64  
 6   Department-2005     1085 non-null   object 
 7   Municipality-2005   1085 non-null   object 
 8   Total 2005          1085 non-null   int64  
 9   Households 2005     1085 non-null   float64
dtypes: float64(1), int64(5), object(4)
memory usage: 93.2+ KB


So far, can be concluded that there are 1077 municipalities out of 1122 in census 2018, common to both census with census information.

#### 1b. Data Preparation

Now, getting ready census table for georeferencing analysis

In [ ]:
# Dropping unnecesary data 
census.drop(columns=['Department-2005', 'Municipality-2005'], inplace=True)

# Checking data types
census.info()

<class 'pandas.core.frame.DataFrame'>
Index: 1085 entries, Medellín, Antioquia to Cumaribo, Vichada
Data columns (total 8 columns):
 #   Column              Non-Null Count  Dtype  
---  ------              --------------  -----  
 0   Department-2018     1085 non-null   object 
 1   Municipality-2018   1085 non-null   object 
 2   Total 2018          1085 non-null   int64  
 3   Housing units 2018  1085 non-null   int64  
 4   Households 2018     1085 non-null   int64  
 5   People 2018         1085 non-null   int64  
 6   Total 2005          1085 non-null   int64  
 7   Households 2005     1085 non-null   float64
dtypes: float64(1), int64(5), object(2)
memory usage: 76.3+ KB


In [ ]:
census

Department-2018 Municipality-2018  Total 2018  \
Location                                                                
Medellín, Antioquia           Antioquia          Medellín     2427129   
Abejorral, Antioquia          Antioquia         Abejorral       20367   
Abriaquí, Antioquia           Antioquia          Abriaquí        2695   
Alejandría, Antioquia         Antioquia        Alejandría        4657   
Amagá, Antioquia              Antioquia             Amagá       30227   
...                                 ...               ...         ...   
Caruru, Vaupés                   Vaupés            Caruru        2915   
Taraira, Vaupés                  Vaupés           Taraira        2215   
Puerto Carreño, Vichada         Vichada    Puerto Carreño       20936   
Santa Rosalía, Vichada          Vichada     Santa Rosalía        4059   
Cumaribo, Vichada               Vichada          Cumaribo       72691   

                         Housing units 2018  Households 2018  People 2018  \
Location                                                                    
Medellín, Antioquia                  892151           815493      2372330   
Abejorral, Antioquia                   8511             6028        17599   
Abriaquí, Antioquia                    1056              776         2159   
Alejandría, Antioquia                  2155             1384         3839   
Amagá, Antioquia                      11638             8884        26821   
...                                     ...              ...          ...   
Caruru, Vaupés                          535              537         2827   
Taraira, Vaupés                         402              411         2010   
Puerto Carreño, Vichada                6866             5816        19788   
Santa Rosalía, Vichada                 1130             1074         4026   
Cumaribo, Vichada                      9476             9533        43138   

                         Total 2005  Households 2005  
Location                                              
Medellín, Antioquia         2219861         605192.0  
Abejorral, Antioquia          19893           5064.0  
Abriaquí, Antioquia            2173            579.0  
Alejandría, Antioquia          3730           1045.0  
Amagá, Antioquia              27115           6928.0  
...                             ...              ...  
Caruru, Vaupés                  641            110.0  
Taraira, Vaupés                1015            226.0  
Puerto Carreño, Vichada       12897           2804.0  
Santa Rosalía, Vichada         3188            584.0  
Cumaribo, Vichada             23990           4967.0  

[1085 rows x 8 columns]

A **Population Anual Variation** is wanted to understand the needs of housing, as a first step.

In [ ]:
year1 = 2005
year2 = 2018
numberYears = year2-year1
df = census.apply(lambda x: ((1+((x[2]-x[6])/x[6]))**(1/numberYears))-1, axis=1)
df= pd.DataFrame(df, columns=['var_pop'])
df

var_pop
Location                         
Medellín, Antioquia      0.006890
Abejorral, Antioquia     0.001813
Abriaquí, Antioquia      0.016699
Alejandría, Antioquia    0.017221
Amagá, Antioquia         0.008393
...                           ...
Caruru, Vaupés           0.123566
Taraira, Vaupés          0.061866
Puerto Carreño, Vichada  0.037970
Santa Rosalía, Vichada   0.018754
Cumaribo, Vichada        0.089017

[1085 rows x 1 columns]

In [ ]:
frames = [census, df]
census = pd.concat(frames, axis=1, join='inner')
census

Department-2018 Municipality-2018  Total 2018  \
Location                                                                
Medellín, Antioquia           Antioquia          Medellín     2427129   
Abejorral, Antioquia          Antioquia         Abejorral       20367   
Abriaquí, Antioquia           Antioquia          Abriaquí        2695   
Alejandría, Antioquia         Antioquia        Alejandría        4657   
Amagá, Antioquia              Antioquia             Amagá       30227   
...                                 ...               ...         ...   
Caruru, Vaupés                   Vaupés            Caruru        2915   
Taraira, Vaupés                  Vaupés           Taraira        2215   
Puerto Carreño, Vichada         Vichada    Puerto Carreño       20936   
Santa Rosalía, Vichada          Vichada     Santa Rosalía        4059   
Cumaribo, Vichada               Vichada          Cumaribo       72691   

                         Housing units 2018  Households 2018  People 2018  \
Location                                                                    
Medellín, Antioquia                  892151           815493      2372330   
Abejorral, Antioquia                   8511             6028        17599   
Abriaquí, Antioquia                    1056              776         2159   
Alejandría, Antioquia                  2155             1384         3839   
Amagá, Antioquia                      11638             8884        26821   
...                                     ...              ...          ...   
Caruru, Vaupés                          535              537         2827   
Taraira, Vaupés                         402              411         2010   
Puerto Carreño, Vichada                6866             5816        19788   
Santa Rosalía, Vichada                 1130             1074         4026   
Cumaribo, Vichada                      9476             9533        43138   

                         Total 2005  Households 2005   var_pop  
Location                                                        
Medellín, Antioquia         2219861         605192.0  0.006890  
Abejorral, Antioquia          19893           5064.0  0.001813  
Abriaquí, Antioquia            2173            579.0  0.016699  
Alejandría, Antioquia          3730           1045.0  0.017221  
Amagá, Antioquia              27115           6928.0  0.008393  
...                             ...              ...       ...  
Caruru, Vaupés                  641            110.0  0.123566  
Taraira, Vaupés                1015            226.0  0.061866  
Puerto Carreño, Vichada       12897           2804.0  0.037970  
Santa Rosalía, Vichada         3188            584.0  0.018754  
Cumaribo, Vichada             23990           4967.0  0.089017  

[1085 rows x 9 columns]

Likewise, A **Households Anual Variation** is wanted to understand the needs of housing.

In [ ]:
df = census.apply(lambda x: ((1+((x[4]-x[7])/x[7]))**(1/numberYears))-1, axis=1)
df= pd.DataFrame(df, columns=['var_households'])
df

var_households
Location                               
Medellín, Antioquia            0.023207
Abejorral, Antioquia           0.013495
Abriaquí, Antioquia            0.022783
Alejandría, Antioquia          0.021848
Amagá, Antioquia               0.019313
...                                 ...
Caruru, Vaupés                 0.129712
Taraira, Vaupés                0.047079
Puerto Carreño, Vichada        0.057725
Santa Rosalía, Vichada         0.047980
Cumaribo, Vichada              0.051428

[1085 rows x 1 columns]

In [ ]:
frames = [census, df]
census = pd.concat(frames, axis=1, join='inner')
census

Department-2018 Municipality-2018  Total 2018  \
Location                                                                
Medellín, Antioquia           Antioquia          Medellín     2427129   
Abejorral, Antioquia          Antioquia         Abejorral       20367   
Abriaquí, Antioquia           Antioquia          Abriaquí        2695   
Alejandría, Antioquia         Antioquia        Alejandría        4657   
Amagá, Antioquia              Antioquia             Amagá       30227   
...                                 ...               ...         ...   
Caruru, Vaupés                   Vaupés            Caruru        2915   
Taraira, Vaupés                  Vaupés           Taraira        2215   
Puerto Carreño, Vichada         Vichada    Puerto Carreño       20936   
Santa Rosalía, Vichada          Vichada     Santa Rosalía        4059   
Cumaribo, Vichada               Vichada          Cumaribo       72691   

                         Housing units 2018  Households 2018  People 2018  \
Location                                                                    
Medellín, Antioquia                  892151           815493      2372330   
Abejorral, Antioquia                   8511             6028        17599   
Abriaquí, Antioquia                    1056              776         2159   
Alejandría, Antioquia                  2155             1384         3839   
Amagá, Antioquia                      11638             8884        26821   
...                                     ...              ...          ...   
Caruru, Vaupés                          535              537         2827   
Taraira, Vaupés                         402              411         2010   
Puerto Carreño, Vichada                6866             5816        19788   
Santa Rosalía, Vichada                 1130             1074         4026   
Cumaribo, Vichada                      9476             9533        43138   

                         Total 2005  Households 2005   var_pop  var_households  
Location                                                                        
Medellín, Antioquia         2219861         605192.0  0.006890        0.023207  
Abejorral, Antioquia          19893           5064.0  0.001813        0.013495  
Abriaquí, Antioquia            2173            579.0  0.016699        0.022783  
Alejandría, Antioquia          3730           1045.0  0.017221        0.021848  
Amagá, Antioquia              27115           6928.0  0.008393        0.019313  
...                             ...              ...       ...             ...  
Caruru, Vaupés                  641            110.0  0.123566        0.129712  
Taraira, Vaupés                1015            226.0  0.061866        0.047079  
Puerto Carreño, Vichada       12897           2804.0  0.037970        0.057725  
Santa Rosalía, Vichada         3188            584.0  0.018754        0.047980  
Cumaribo, Vichada             23990           4967.0  0.089017        0.051428  

[1085 rows x 10 columns]

Finally, the ratio between households and  housing units in census 2018

In [ ]:
df = census.apply(lambda x: x[4]/x[3], axis=1)
df= pd.DataFrame(df, columns=['household/housing ratio'])
df

household/housing ratio
Location                                        
Medellín, Antioquia                     0.914075
Abejorral, Antioquia                    0.708260
Abriaquí, Antioquia                     0.734848
Alejandría, Antioquia                   0.642227
Amagá, Antioquia                        0.763361
...                                          ...
Caruru, Vaupés                          1.003738
Taraira, Vaupés                         1.022388
Puerto Carreño, Vichada                 0.847073
Santa Rosalía, Vichada                  0.950442
Cumaribo, Vichada                       1.006015

[1085 rows x 1 columns]

In [ ]:
frames = [census, df]
census = pd.concat(frames, axis=1, join='inner')
census

Department-2018 Municipality-2018  Total 2018  \
Location                                                                
Medellín, Antioquia           Antioquia          Medellín     2427129   
Abejorral, Antioquia          Antioquia         Abejorral       20367   
Abriaquí, Antioquia           Antioquia          Abriaquí        2695   
Alejandría, Antioquia         Antioquia        Alejandría        4657   
Amagá, Antioquia              Antioquia             Amagá       30227   
...                                 ...               ...         ...   
Caruru, Vaupés                   Vaupés            Caruru        2915   
Taraira, Vaupés                  Vaupés           Taraira        2215   
Puerto Carreño, Vichada         Vichada    Puerto Carreño       20936   
Santa Rosalía, Vichada          Vichada     Santa Rosalía        4059   
Cumaribo, Vichada               Vichada          Cumaribo       72691   

                         Housing units 2018  Households 2018  People 2018  \
Location                                                                    
Medellín, Antioquia                  892151           815493      2372330   
Abejorral, Antioquia                   8511             6028        17599   
Abriaquí, Antioquia                    1056              776         2159   
Alejandría, Antioquia                  2155             1384         3839   
Amagá, Antioquia                      11638             8884        26821   
...                                     ...              ...          ...   
Caruru, Vaupés                          535              537         2827   
Taraira, Vaupés                         402              411         2010   
Puerto Carreño, Vichada                6866             5816        19788   
Santa Rosalía, Vichada                 1130             1074         4026   
Cumaribo, Vichada                      9476             9533        43138   

                         Total 2005  Households 2005   var_pop  \
Location                                                         
Medellín, Antioquia         2219861         605192.0  0.006890   
Abejorral, Antioquia          19893           5064.0  0.001813   
Abriaquí, Antioquia            2173            579.0  0.016699   
Alejandría, Antioquia          3730           1045.0  0.017221   
Amagá, Antioquia              27115           6928.0  0.008393   
...                             ...              ...       ...   
Caruru, Vaupés                  641            110.0  0.123566   
Taraira, Vaupés                1015            226.0  0.061866   
Puerto Carreño, Vichada       12897           2804.0  0.037970   
Santa Rosalía, Vichada         3188            584.0  0.018754   
Cumaribo, Vichada             23990           4967.0  0.089017   

                         var_households  household/housing ratio  
Location                                                          
Medellín, Antioquia            0.023207                 0.914075  
Abejorral, Antioquia           0.013495                 0.708260  
Abriaquí, Antioquia            0.022783                 0.734848  
Alejandría, Antioquia          0.021848                 0.642227  
Amagá, Antioquia               0.019313                 0.763361  
...                                 ...                      ...  
Caruru, Vaupés                 0.129712                 1.003738  
Taraira, Vaupés                0.047079                 1.022388  
Puerto Carreño, Vichada        0.057725                 0.847073  
Santa Rosalía, Vichada         0.047980                 0.950442  
Cumaribo, Vichada              0.051428                 1.006015  

[1085 rows x 11 columns]

In [ ]:
stat=census.describe()
stat

Total 2018  Housing units 2018  Households 2018   People 2018  \
count  1.085000e+03        1.085000e+03     1.085000e+03  1.085000e+03   
mean   4.396885e+04        1.470271e+04     1.302189e+04  4.035663e+04   
std    2.579564e+05        8.739226e+04     8.504882e+04  2.464542e+05   
min    1.097000e+03        3.980000e+02     3.210000e+02  9.030000e+02   
25%    6.729000e+03        2.573000e+03     2.032000e+03  6.114000e+03   
50%    1.299500e+04        4.527000e+03     3.752000e+03  1.159900e+04   
75%    2.729200e+04        9.020000e+03     7.576000e+03  2.459300e+04   
max    7.412566e+06        2.523519e+06     2.514482e+06  7.181469e+06   

         Total 2005  Households 2005      var_pop  var_households  \
count  1.085000e+03     1.085000e+03  1085.000000     1085.000000   
mean   3.796741e+04     9.686468e+03     0.008455        0.021393   
std    2.346136e+05     6.562750e+04     0.019968        0.018864   
min    6.410000e+02     1.100000e+02    -0.055628       -0.043776   
25%    6.462000e+03     1.598000e+03    -0.002776        0.009299   
50%    1.166900e+04     2.841000e+03     0.006453        0.019330   
75%    2.330800e+04     5.528000e+03     0.017296        0.030434   
max    6.778691e+06     1.931372e+06     0.160445        0.159726   

       household/housing ratio  
count              1085.000000  
mean                  0.830204  
std                   0.138395  
min                   0.288020  
25%                   0.741120  
50%                   0.827929  
75%                   0.912106  
max                   1.341361

We can conclude so far that **population annual variation ** has a mean value of (0.84% growing per year), while **households annual variation** has mean value of (2.12% growing per year), indicating that householdes is growing at faster rate, more than twice of population.

The mean value of **household/housing ratio** of 82% in 2018 shows that may be enough housing units for households; however housing market should growth at least at this rate of 2.12% per year.

A **standard deviation** around 2% are common to both set of data, showing that the distribution of variation is highly concentrated aorund its mean.

#### 1c. National sociodemographics georeferenced analysis

Use geopy library to get the latitude and longitude values of Colombia.

In [ ]:
address = 'Colombia'

# Geolocation is a simple and clever application which uses google maps api.
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude

print('The geograpical coordinate of Supia are {}, {}.'.format(latitude, longitude))
print(location.raw)

The geograpical coordinate of Supia are 2.8894434, -73.783892.
{'place_id': 258355394, 'licence': 'Data © OpenStreetMap contributors, ODbL 1.0. https://osm.org/copyright', 'osm_type': 'relation', 'osm_id': 120027, 'boundingbox': ['-4.2316872', '16.0571269', '-82.1243666', '-66.8511571'], 'lat': '2.8894434', 'lon': '-73.783892', 'display_name': 'Colombia', 'class': 'boundary', 'type': 'administrative', 'importance': 0.8897086469365706, 'icon': 'https://nominatim.openstreetmap.org/ui/mapicons//poi_boundary_administrative.p.20.png'}


Let's get the geographical coordinates of Municipalities

In [ ]:
# Convenient function to delay between geocoding calls
geocode = RateLimiter(geolocator.geocode, min_delay_seconds=1)
#geocode = lambda query: geolocator.geocode("%s" % query)

df=census
df.reset_index(inplace=True)
df['location'] = df['Location'].apply(geocode)
df['point'] = df['location'].apply(lambda loc: tuple(loc.point) if loc else None)

# Split point column into latitude, longitude and altitude columns
df[['latitude', 'longitude', 'altitude']] = pd.DataFrame(df['point'].tolist(), index=df.index)

#census.head()
df

Location Department-2018 Municipality-2018  Total 2018  \
0         Medellín, Antioquia       Antioquia          Medellín     2427129   
1        Abejorral, Antioquia       Antioquia         Abejorral       20367   
2         Abriaquí, Antioquia       Antioquia          Abriaquí        2695   
3       Alejandría, Antioquia       Antioquia        Alejandría        4657   
4            Amagá, Antioquia       Antioquia             Amagá       30227   
...                       ...             ...               ...         ...   
1080           Caruru, Vaupés          Vaupés            Caruru        2915   
1081          Taraira, Vaupés          Vaupés           Taraira        2215   
1082  Puerto Carreño, Vichada         Vichada    Puerto Carreño       20936   
1083   Santa Rosalía, Vichada         Vichada     Santa Rosalía        4059   
1084        Cumaribo, Vichada         Vichada          Cumaribo       72691   

      Housing units 2018  Households 2018  People 2018  Total 2005  \
0                 892151           815493      2372330     2219861   
1                   8511             6028        17599       19893   
2                   1056              776         2159        2173   
3                   2155             1384         3839        3730   
4                  11638             8884        26821       27115   
...                  ...              ...          ...         ...   
1080                 535              537         2827         641   
1081                 402              411         2010        1015   
1082                6866             5816        19788       12897   
1083                1130             1074         4026        3188   
1084                9476             9533        43138       23990   

      Households 2005   var_pop  var_households  household/housing ratio  \
0            605192.0  0.006890        0.023207                 0.914075   
1              5064.0  0.001813        0.013495                 0.708260   
2               579.0  0.016699        0.022783                 0.734848   
3              1045.0  0.017221        0.021848                 0.642227   
4              6928.0  0.008393        0.019313                 0.763361   
...               ...       ...             ...                      ...   
1080            110.0  0.123566        0.129712                 1.003738   
1081            226.0  0.061866        0.047079                 1.022388   
1082           2804.0  0.037970        0.057725                 0.847073   
1083            584.0  0.018754        0.047980                 0.950442   
1084           4967.0  0.089017        0.051428                 1.006015   

                                               location  \
0     (Medellín, Valle de Aburrá, Antioquia, Región ...   
1     (Abejorral, Oriente, Antioquia, Región Andina,...   
2     (Abriaquí, Occidente, Antioquia, Región Andina...   
3     (Alejandría, Oriente, Antioquia, Región Andina...   
4     (Amagá, Suroeste, Antioquia, Región Andina, Co...   
...                                                 ...   
1080  (Carurú, Vaupés, Amazonia, Colombia, (1.015525...   
1081  (Taraira, Vaupés, Amazonia, Colombia, (-0.6875...   
1082  (Puerto Carreño, Vichada, Orinoquia, 990001-99...   
1083  (Santa Rosalía, Vichada, Orinoquia, Colombia, ...   
1084  (Cumaribo, Vichada, Orinoquia, Colombia, (4.44...   

                                              point  latitude  longitude  \
0                      (6.2443382, -75.573553, 0.0)  6.244338 -75.573553   
1              (5.8049504, -75.42984181835139, 0.0)  5.804950 -75.429842   
2             (6.62847905, -76.08327037406424, 0.0)  6.628479 -76.083270   
3     (6.3557801000000005, -75.09866249389314, 0.0)  6.355780 -75.098662   
4                  (6.0358169, -75.7009108125, 0.0)  6.035817 -75.700911   
...                                             ...       ...        ...   
1080                  (1.0155254, -71.2961479, 0.0)  1.015525 -71.296148   
1

In [ ]:
# Drop not assigned values
census = census.dropna() 
census

Location Department-2018 Municipality-2018  Total 2018  \
0         Medellín, Antioquia       Antioquia          Medellín     2427129   
1        Abejorral, Antioquia       Antioquia         Abejorral       20367   
2         Abriaquí, Antioquia       Antioquia          Abriaquí        2695   
3       Alejandría, Antioquia       Antioquia        Alejandría        4657   
4            Amagá, Antioquia       Antioquia             Amagá       30227   
...                       ...             ...               ...         ...   
1080           Caruru, Vaupés          Vaupés            Caruru        2915   
1081          Taraira, Vaupés          Vaupés           Taraira        2215   
1082  Puerto Carreño, Vichada         Vichada    Puerto Carreño       20936   
1083   Santa Rosalía, Vichada         Vichada     Santa Rosalía        4059   
1084        Cumaribo, Vichada         Vichada          Cumaribo       72691   

      Housing units 2018  Households 2018  People 2018  Total 2005  \
0                 892151           815493      2372330     2219861   
1                   8511             6028        17599       19893   
2                   1056              776         2159        2173   
3                   2155             1384         3839        3730   
4                  11638             8884        26821       27115   
...                  ...              ...          ...         ...   
1080                 535              537         2827         641   
1081                 402              411         2010        1015   
1082                6866             5816        19788       12897   
1083                1130             1074         4026        3188   
1084                9476             9533        43138       23990   

      Households 2005   var_pop  var_households  household/housing ratio  \
0            605192.0  0.006890        0.023207                 0.914075   
1              5064.0  0.001813        0.013495                 0.708260   
2               579.0  0.016699        0.022783                 0.734848   
3              1045.0  0.017221        0.021848                 0.642227   
4              6928.0  0.008393        0.019313                 0.763361   
...               ...       ...             ...                      ...   
1080            110.0  0.123566        0.129712                 1.003738   
1081            226.0  0.061866        0.047079                 1.022388   
1082           2804.0  0.037970        0.057725                 0.847073   
1083            584.0  0.018754        0.047980                 0.950442   
1084           4967.0  0.089017        0.051428                 1.006015   

                                               location  \
0     (Medellín, Valle de Aburrá, Antioquia, Región ...   
1     (Abejorral, Oriente, Antioquia, Región Andina,...   
2     (Abriaquí, Occidente, Antioquia, Región Andina...   
3     (Alejandría, Oriente, Antioquia, Región Andina...   
4     (Amagá, Suroeste, Antioquia, Región Andina, Co...   
...                                                 ...   
1080  (Carurú, Vaupés, Amazonia, Colombia, (1.015525...   
1081  (Taraira, Vaupés, Amazonia, Colombia, (-0.6875...   
1082  (Puerto Carreño, Vichada, Orinoquia, 990001-99...   
1083  (Santa Rosalía, Vichada, Orinoquia, Colombia, ...   
1084  (Cumaribo, Vichada, Orinoquia, Colombia, (4.44...   

                                              point  latitude  longitude  \
0                      (6.2443382, -75.573553, 0.0)  6.244338 -75.573553   
1              (5.8049504, -75.42984181835139, 0.0)  5.804950 -75.429842   
2             (6.62847905, -76.08327037406424, 0.0)  6.628479 -76.083270   
3     (6.3557801000000005, -75.09866249389314, 0.0)  6.355780 -75.098662   
4                  (6.0358169, -75.7009108125, 0.0)  6.035817 -75.700911   
...                                             ...       ...        ...   
1080                  (1.0155254, -71.2961479, 0.0)  1.015525 -71.296148   
1

Saving data consolidated and prepared in a csv file

In [ ]:
fileName="census.csv" #name of the CSV file generated
census.to_csv(fileName, index=False)

Defining groups of data for **population annual variation** at steps of 25% each

In [ ]:
varmax = census['var_pop'].max()
varmin = census['var_pop'].min()
var025=stat.iloc[4,6]
var050=stat.iloc[5,6]
var075=stat.iloc[6,6]
var100=stat.iloc[7,6]
pav = [var025, var050, var075, var100]
print(pav)

[-0.002775889647389951, 0.00645314280840692, 0.01729556286220313, 0.16044511053793986]


Defining groups of data for **households annual variation** at steps of 25% each

In [ ]:
varmax = census['var_households'].max()
varmin = census['var_households'].min()
var025=stat.iloc[4,7]
var050=stat.iloc[5,7]
var075=stat.iloc[6,7]
var100=stat.iloc[7,7]
hav = [var025, var050, var075, var100]
print(hav)

[0.009299381249901817, 0.019330306898952765, 0.03043414818689394, 0.15972644531332625]


Defining groups of data for **households/housing ratio** at steps of 25% each

In [ ]:
varmax = census['household/housing ratio'].max()
varmin = census['household/housing ratio'].min()
var025=stat.iloc[4,8]
var050=stat.iloc[5,8]
var075=stat.iloc[6,8]
var100=stat.iloc[7,8]
hhr = [var025, var050, var075, var100]
print(hhr)

[0.7411202185792349, 0.827928524156188, 0.912106135986733, 1.3413605203023378]


#### Creating folium map for population annual variation

In [ ]:
# create map of population annual variation using latitude and longitude values
map = folium.Map(location=[latitude, longitude], zoom_start=5)

# add markers "Municipalities" to map
for label, lat, lng, var, tot in zip(census['Location'], census['latitude'], census['longitude'], census['var_pop'], census['Total 2018']):
    label = '{}, {:.2f}'.format(label, var) 
    label = folium.Popup(label, parse_html=True)
    
    if var<=0:
        color='red'
        radius=4
        fill=False
    elif var<=pav[1]:
        color='grey'
        radius=4
        fill=False        
    elif var<=pav[2]:
        color='orange'
        radius=4
        fill=False        
    elif var<=pav[3]:
        color='cyan'
        radius=4
        fill=False        
    else: 
        color='yellow'    
    
    folium.CircleMarker(
        [lat, lng],
        radius=radius,
        popup=label,
        color=color,
        fill=fill,
        fill_color=color,
        fill_opacity=0.7,
        parse_html=False).add_to(map)

map

The **population annual variation map** shows population decreasing from several municipalities along the mountain region of the country.  On the other hand municipalities toward west country are growing at higher pace. 

#### Creating folium map for households annual variation

In [ ]:
# create map of househlods annual variation using latitude and longitude values
map = folium.Map(location=[latitude, longitude], zoom_start=5)

# add markers "Municipalities" to map
for label, lat, lng, var, tot in zip(census['Location'], census['latitude'], census['longitude'], census['var_households'], census['Total 2018']):
    label = '{}, {:.2f}'.format(label, var) 
    label = folium.Popup(label, parse_html=True)
    
    if var<=0:
        color='red'
        radius=4
        fill=False
    elif var<=hav[1]:
        color='grey'
        radius=4
        fill=False        
    elif var<=hav[2]:
        color='orange'
        radius=4
        fill=False        
    elif var<=hav[3]:
        color='cyan'
        radius=4
        fill=False        
    else: 
        color='yellow'    
    
    folium.CircleMarker(
        [lat, lng],
        radius=radius,
        popup=label,
        color=color,
        fill=fill,
        fill_color=color,
        fill_opacity=0.7,
        parse_html=False).add_to(map)

map

The **household annual variation map** shows householdes increasing at faster pace.

#### Creating folium map for households/housing ratio

In [ ]:
# create map of hosuehlds/housing ratio using latitude and longitude values
map = folium.Map(location=[latitude, longitude], zoom_start=5)

# add markers "Municipalities" to map
for label, lat, lng, var, tot in zip(census['Location'], census['latitude'], census['longitude'], census['household/housing ratio'], census['Total 2018']):
    label = '{}, {:.2f}'.format(label, var) 
    label = folium.Popup(label, parse_html=True)
    
    if var<=hhr[0]:
        color='red'
        radius=4
        fill=False
    elif var<=hhr[1]:
        color='grey'
        radius=4
        fill=False        
    elif var<=hhr[2]:
        color='orange'
        radius=4
        fill=False        
    elif var<=hhr[3]:
        color='cyan'
        radius=4
        fill=False        
    else: 
        color='yellow'    
    
    folium.CircleMarker(
        [lat, lng],
        radius=radius,
        popup=label,
        color=color,
        fill=fill,
        fill_color=color,
        fill_opacity=0.7,
        parse_html=False).add_to(map)

map

#### Conclusion: National sociodemographics georeferenced analysis

There is a greater annual variation by households than by population, with a mean  of 3.04%; the north, east and south-western regions of Colombia vary at a higher rate (higher demand for housing); in contrast to the cordillera region, with a variation of households less than 1.88%.

---

### 2. Environmental analysis (economic sector)
#### Download and Explore Dataset Construction Sector

**Downloading the latest ICCV (Home Construction Cost Index), IPC(Consumer Price Index), IPVN (New Home Price Index)** from the national statistics department, DANE, in order to get an insgiht of the behavoiour of the construcion prices in the country.

#### ICCV

In [ ]:
# Read data from CSV file
os.listdir(os.getcwd())
df_iccv = pd.read_csv('iccv2021.csv')
df_iccv.head()

Department          City  2017  2018  2019  2020  2021
0     Antioquia      Medellín  5.07  3.95  2.73  4.69  5.96
1     Atlántico  Barranquilla  2.98  2.06  2.59  2.13  7.21
2  Bogotá, D.C.  Bogotá, D.C.  3.80  2.35  2.07  3.27  3.63
3       Bolívar     Cartagena  2.15  2.39  2.01  2.96  5.99
4        Caldas     Manizales  4.21  4.76  3.06  5.77  5.64

#### Data Preparation

In [ ]:
mun=df_iccv['City']+', '+df_iccv['Department']
mun = pd.DataFrame(mun, columns=['Location'])

df_iccv[['Location']] = mun[['Location']]
df_iccv.drop(['Department', 'City'], axis=1, inplace=True)
df_iccv

2017  2018  2019  2020  2021                    Location
0   5.07  3.95  2.73  4.69  5.96         Medellín, Antioquia
1   2.98  2.06  2.59  2.13  7.21     Barranquilla, Atlántico
2   3.80  2.35  2.07  3.27  3.63  Bogotá, D.C., Bogotá, D.C.
3   2.15  2.39  2.01  2.96  5.99          Cartagena, Bolívar
4   4.21  4.76  3.06  5.77  5.64           Manizales, Caldas
5   3.59  1.51  2.49  2.94  7.79              Popayán, Cauca
6   2.19  3.09  0.90  3.38  8.77                Neiva, Huila
7   1.16  4.59  1.88  2.64  5.72      Santa Marta, Magdalena
8   4.31  4.85  2.80  3.20  6.81               Pasto, Nariño
9   2.74  1.98  2.07  2.15  5.50  Cúcuta, Norte de Santander
10  5.85  3.31  3.29  2.52  8.39            Armenia, Quindío
11  4.86  3.75  3.88  3.57  8.18          Pereira, Risaralda
12  1.99  3.48  2.73  4.01  7.90      Bucaramanga, Santander
13  1.78  2.96  2.07  1.83  5.78              Ibagué, Tolima
14  5.49  3.74  2.97  3.31  6.56       Cali, Valle del Cauca

In [ ]:
df = df_iccv
if(df.index.name != 'Location'):
    df = df.set_index('Location')

df_t=df.transpose()
df_t

Location  Medellín, Antioquia  Barranquilla, Atlántico  \
2017                     5.07                     2.98   
2018                     3.95                     2.06   
2019                     2.73                     2.59   
2020                     4.69                     2.13   
2021                     5.96                     7.21   

Location  Bogotá, D.C., Bogotá, D.C.  Cartagena, Bolívar  Manizales, Caldas  \
2017                            3.80                2.15               4.21   
2018                            2.35                2.39               4.76   
2019                            2.07                2.01               3.06   
2020                            3.27                2.96               5.77   
2021                            3.63                5.99               5.64   

Location  Popayán, Cauca  Neiva, Huila  Santa Marta, Magdalena  Pasto, Nariño  \
2017                3.59          2.19                    1.16           4.31   
2018                1.51          3.09                    4.59           4.85   
2019                2.49          0.90                    1.88           2.80   
2020                2.94          3.38                    2.64           3.20   
2021                7.79          8.77                    5.72           6.81   

Location  Cúcuta, Norte de Santander  Armenia, Quindío  Pereira, Risaralda  \
2017                            2.74              5.85                4.86   
2018                            1.98              3.31                3.75   
2019                            2.07              3.29                3.88   
2020                            2.15              2.52                3.57   
2021                            5.50              8.39                8.18   

Location  Bucaramanga, Santander  Ibagué, Tolima  Cali, Valle del Cauca  
2017                        1.99            1.78                   5.49  
2018                        3.48            2.96                   3.74  
2019                        2.73            2.07                   2.97  
2020                        4.01            1.83                   3.31  
2021                        7.90            5.78                   6.56

#### An iccv annual variation trend is estimated for each city

In [ ]:
numberYears = len(df_t)
n = np.linspace(1,numberYears,numberYears)
y=df_t
z = np.polyfit(n,y,1).transpose()
df = pd.DataFrame(z, columns=['coeff1_iccv', 'coeff2_iccv'])
df

coeff1_iccv  coeff2_iccv
0         0.252        3.724
1         0.853        0.835
2         0.058        2.850
3         0.825        0.625
4         0.387        3.527
5         0.983        0.715
6         1.345       -0.369
7         0.717        1.047
8         0.335        3.389
9         0.569        1.181
10        0.429        3.385
11        0.646        2.910
12        1.235        0.317
13        0.687        0.823
14        0.171        3.901

In [ ]:
frames = [df_iccv, df]
df_iccv = pd.concat(frames, axis=1, join='inner')

if(df_iccv.index.name != 'Location'):
    df_iccv = df_iccv.set_index('Location')
    
df_iccv

2017  2018  2019  2020  2021  coeff1_iccv  \
Location                                                                
Medellín, Antioquia         5.07  3.95  2.73  4.69  5.96        0.252   
Barranquilla, Atlántico     2.98  2.06  2.59  2.13  7.21        0.853   
Bogotá, D.C., Bogotá, D.C.  3.80  2.35  2.07  3.27  3.63        0.058   
Cartagena, Bolívar          2.15  2.39  2.01  2.96  5.99        0.825   
Manizales, Caldas           4.21  4.76  3.06  5.77  5.64        0.387   
Popayán, Cauca              3.59  1.51  2.49  2.94  7.79        0.983   
Neiva, Huila                2.19  3.09  0.90  3.38  8.77        1.345   
Santa Marta, Magdalena      1.16  4.59  1.88  2.64  5.72        0.717   
Pasto, Nariño               4.31  4.85  2.80  3.20  6.81        0.335   
Cúcuta, Norte de Santander  2.74  1.98  2.07  2.15  5.50        0.569   
Armenia, Quindío            5.85  3.31  3.29  2.52  8.39        0.429   
Pereira, Risaralda          4.86  3.75  3.88  3.57  8.18        0.646   
Bucaramanga, Santander      1.99  3.48  2.73  4.01  7.90        1.235   
Ibagué, Tolima              1.78  2.96  2.07  1.83  5.78        0.687   
Cali, Valle del Cauca       5.49  3.74  2.97  3.31  6.56        0.171   

                            coeff2_iccv  
Location                                 
Medellín, Antioquia               3.724  
Barranquilla, Atlántico           0.835  
Bogotá, D.C., Bogotá, D.C.        2.850  
Cartagena, Bolívar                0.625  
Manizales, Caldas                 3.527  
Popayán, Cauca                    0.715  
Neiva, Huila                     -0.369  
Santa Marta, Magdalena            1.047  
Pasto, Nariño                     3.389  
Cúcuta, Norte de Santander        1.181  
Armenia, Quindío                  3.385  
Pereira, Risaralda                2.910  
Bucaramanga, Santander            0.317  
Ibagué, Tolima                    0.823  
Cali, Valle del Cauca             3.901

In [ ]:
stat_iccv = df_iccv.describe()
stat_iccv

2017       2018       2019       2020       2021  coeff1_iccv  \
count  15.000000  15.000000  15.000000  15.000000  15.000000    15.000000   
mean    3.478000   3.251333   2.502667   3.224667   6.655333     0.632800   
std     1.467477   1.048406   0.707414   1.024129   1.390487     0.375263   
min     1.160000   1.510000   0.900000   1.830000   3.630000     0.058000   
25%     2.170000   2.370000   2.070000   2.580000   5.750000     0.361000   
50%     3.590000   3.310000   2.590000   3.200000   6.560000     0.646000   
75%     4.585000   3.850000   2.885000   3.475000   7.845000     0.839000   
max     5.850000   4.850000   3.880000   5.770000   8.770000     1.345000   

       coeff2_iccv  
count    15.000000  
mean      1.924000  
std       1.476899  
min      -0.369000  
25%       0.769000  
50%       1.181000  
75%       3.387000  
max       3.901000

#### Defining groups of data for **iccv** at steps of 25% each

In [ ]:
varmax = df_iccv['coeff1_iccv'].max()
varmin = df_iccv['coeff1_iccv'].min()
var025=stat_iccv.iloc[4,5]
var050=stat_iccv.iloc[5,5]
var075=stat_iccv.iloc[6,5]
var100=stat_iccv.iloc[7,5]
iccvav = [var025, var050, var075, var100]
print(iccvav)

[0.3610000000000001, 0.6459999999999997, 0.8389999999999997, 1.3449999999999998]


#### IPC

In [ ]:
# Read data from CSV file
os.listdir(os.getcwd())
df_ipc = pd.read_csv('ipc2021.csv')
df_ipc.head()

Department          City  2017  2018  2019  2020  2021
0     Antioquia      Medellín  4.16  3.69  4.49  2.58  1.99
1     Atlántico  Barranquilla  3.24  3.69  4.13  2.24  2.86
2  Bogotá, D.C.  Bogotá, D.C.  4.63  3.06  3.49  1.17  1.95
3       Bolívar     Cartagena  3.17  3.45  3.88  0.35  2.05
4        Boyacá         Tunja  3.35  3.37  3.90  1.34  1.79

#### Data Preparation

In [ ]:
mun=df_ipc['City']+', '+df_ipc['Department']
mun = pd.DataFrame(mun, columns=['Location'])

df_ipc[['Location']] = mun[['Location']]
df_ipc.drop(['Department', 'City'], axis=1, inplace=True)
df_ipc

2017  2018  2019  2020  2021                    Location
0   4.16  3.69  4.49  2.58  1.99         Medellín, Antioquia
1   3.24  3.69  4.13  2.24  2.86     Barranquilla, Atlántico
2   4.63  3.06  3.49  1.17  1.95  Bogotá, D.C., Bogotá, D.C.
3   3.17  3.45  3.88  0.35  2.05          Cartagena, Bolívar
4   3.35  3.37  3.90  1.34  1.79               Tunja, Boyacá
5   4.29  3.31  3.74  2.27  2.47           Manizales, Caldas
6   2.98  2.65  3.94  1.55  1.80          Florencia, Caquetá
7   4.00  2.76  3.71  2.68  2.78              Popayán, Cauca
8   3.41  2.37  3.60  0.91  2.92           Valledupar, Cesar
9   2.79  3.37  3.99  0.77  2.01           Montería, Córdoba
10  2.61  2.84  2.72  1.93  2.05                Neiva, Huila
11  1.28  2.84  4.79  2.30  1.92        Riohacha, La Guajira
12  2.84  2.73  3.83  2.11  2.89      Santa Marta, Magdalena
13  1.78  2.43  2.94  0.97  2.59         Villavicencio, Meta
14  4.00  3.36  3.87  1.10  2.23               Pasto, Nariño
15  2.87  2.89  3.79  2.89  2.79  Cúcuta, Norte de Santander
16  3.78  2.81  4.28  2.54  2.74            Armenia, Quindío
17  4.11  3.17  3.72  2.17  2.66          Pereira, Risaralda
18  3.76  2.79  3.76  1.12  2.69      Bucaramanga, Santander
19  1.67  3.47  3.53  0.93  1.58            Sincelejo, Sucre
20  2.91  3.02  3.37  0.22  2.48              Ibagué, Tolima
21  4.28  3.08  4.53  1.85  2.14       Cali, Valle del Cauca

In [ ]:
df = df_ipc
if(df.index.name != 'Location'):
    df = df.set_index('Location')

df_t=df.transpose()
df_t

Location  Medellín, Antioquia  Barranquilla, Atlántico  \
2017                     4.16                     3.24   
2018                     3.69                     3.69   
2019                     4.49                     4.13   
2020                     2.58                     2.24   
2021                     1.99                     2.86   

Location  Bogotá, D.C., Bogotá, D.C.  Cartagena, Bolívar  Tunja, Boyacá  \
2017                            4.63                3.17           3.35   
2018                            3.06                3.45           3.37   
2019                            3.49                3.88           3.90   
2020                            1.17                0.35           1.34   
2021                            1.95                2.05           1.79   

Location  Manizales, Caldas  Florencia, Caquetá  Popayán, Cauca  \
2017                   4.29                2.98            4.00   
2018                   3.31                2.65            2.76   
2019                   3.74                3.94            3.71   
2020                   2.27                1.55            2.68   
2021                   2.47                1.80            2.78   

Location  Valledupar, Cesar  Montería, Córdoba  ...  Santa Marta, Magdalena  \
2017                   3.41               2.79  ...                    2.84   
2018                   2.37               3.37  ...                    2.73   
2019                   3.60               3.99  ...                    3.83   
2020                   0.91               0.77  ...                    2.11   
2021                   2.92               2.01  ...                    2.89   

Location  Villavicencio, Meta  Pasto, Nariño  Cúcuta, Norte de Santander  \
2017                     1.78           4.00                        2.87   
2018                     2.43           3.36                        2.89   
2019                     2.94           3.87                        3.79   
2020                     0.97           1.10                        2.89   
2021                     2.59           2.23                        2.79   

Location  Armenia, Quindío  Pereira, Risaralda  Bucaramanga, Santander  \
2017                  3.78                4.11                    3.76   
2018                  2.81                3.17                    2.79   
2019                  4.28                3.72                    3.76   
2020                  2.54                2.17                    1.12   
2021                  2.74                2.66                    2.69   

Location  Sincelejo, Sucre  Ibagué, Tolima  Cali, Valle del Cauca  
2017                  1.67            2.91                   4.28  
2018                  3.47            3.02                   3.08  
2019                  3.53            3.37                   4.53  
2020                  0.93            0.22                   1.85  
2021                  1.58            2.48                   2.14  

[5 rows x 22 columns]

#### An ipc annual variation trend is estimated for each city

In [ ]:
numberYears = len(df_t)
n = np.linspace(1,numberYears,numberYears)
y=df_t
z = np.polyfit(n,y,1).transpose()
df = pd.DataFrame(z, columns=['coeff1_ipc', 'coeff2_ipc'])
df

coeff1_ipc  coeff2_ipc
0       -0.545       5.017
1       -0.221       3.895
2       -0.725       5.035
3       -0.534       4.182
4       -0.515       4.295
5       -0.468       4.620
6       -0.346       3.622
7       -0.252       3.942
8       -0.244       3.374
9       -0.416       3.834
10      -0.203       3.039
11       0.074       2.404
12      -0.052       3.036
13       0.016       2.094
14      -0.580       4.652
15      -0.016       3.094
16      -0.235       3.935
17      -0.390       4.336
18      -0.381       3.967
19      -0.272       3.052
20      -0.366       3.498
21      -0.551       4.829

In [ ]:
frames = [df_ipc, df]
df_ipc = pd.concat(frames, axis=1, join='inner')

if(df_ipc.index.name != 'Location'):
    df_ipc = df_ipc.set_index('Location')

df_ipc

2017  2018  2019  2020  2021  coeff1_ipc  \
Location                                                               
Medellín, Antioquia         4.16  3.69  4.49  2.58  1.99      -0.545   
Barranquilla, Atlántico     3.24  3.69  4.13  2.24  2.86      -0.221   
Bogotá, D.C., Bogotá, D.C.  4.63  3.06  3.49  1.17  1.95      -0.725   
Cartagena, Bolívar          3.17  3.45  3.88  0.35  2.05      -0.534   
Tunja, Boyacá               3.35  3.37  3.90  1.34  1.79      -0.515   
Manizales, Caldas           4.29  3.31  3.74  2.27  2.47      -0.468   
Florencia, Caquetá          2.98  2.65  3.94  1.55  1.80      -0.346   
Popayán, Cauca              4.00  2.76  3.71  2.68  2.78      -0.252   
Valledupar, Cesar           3.41  2.37  3.60  0.91  2.92      -0.244   
Montería, Córdoba           2.79  3.37  3.99  0.77  2.01      -0.416   
Neiva, Huila                2.61  2.84  2.72  1.93  2.05      -0.203   
Riohacha, La Guajira        1.28  2.84  4.79  2.30  1.92       0.074   
Santa Marta, Magdalena      2.84  2.73  3.83  2.11  2.89      -0.052   
Villavicencio, Meta         1.78  2.43  2.94  0.97  2.59       0.016   
Pasto, Nariño               4.00  3.36  3.87  1.10  2.23      -0.580   
Cúcuta, Norte de Santander  2.87  2.89  3.79  2.89  2.79      -0.016   
Armenia, Quindío            3.78  2.81  4.28  2.54  2.74      -0.235   
Pereira, Risaralda          4.11  3.17  3.72  2.17  2.66      -0.390   
Bucaramanga, Santander      3.76  2.79  3.76  1.12  2.69      -0.381   
Sincelejo, Sucre            1.67  3.47  3.53  0.93  1.58      -0.272   
Ibagué, Tolima              2.91  3.02  3.37  0.22  2.48      -0.366   
Cali, Valle del Cauca       4.28  3.08  4.53  1.85  2.14      -0.551   

                            coeff2_ipc  
Location                                
Medellín, Antioquia              5.017  
Barranquilla, Atlántico          3.895  
Bogotá, D.C., Bogotá, D.C.       5.035  
Cartagena, Bolívar               4.182  
Tunja, Boyacá                    4.295  
Manizales, Caldas                4.620  
Florencia, Caquetá               3.622  
Popayán, Cauca                   3.942  
Valledupar, Cesar                3.374  
Montería, Córdoba                3.834  
Neiva, Huila                     3.039  
Riohacha, La Guajira             2.404  
Santa Marta, Magdalena           3.036  
Villavicencio, Meta              2.094  
Pasto, Nariño                    4.652  
Cúcuta, Norte de Santander       3.094  
Armenia, Quindío                 3.935  
Pereira, Risaralda               4.336  
Bucaramanga, Santander           3.967  
Sincelejo, Sucre                 3.052  
Ibagué, Tolima                   3.498  
Cali, Valle del Cauca            4.829

In [ ]:
stat_ipc=df_ipc.describe()
stat_ipc

2017       2018       2019       2020       2021  coeff1_ipc  \
count  22.000000  22.000000  22.000000  22.000000  22.000000   22.000000   
mean    3.268636   3.052273   3.818182   1.635909   2.335455   -0.328273   
std     0.899086   0.376234   0.474027   0.785710   0.422055    0.211148   
min     1.280000   2.370000   2.720000   0.220000   1.580000   -0.725000   
25%     2.847500   2.795000   3.627500   1.002500   1.995000   -0.503250   
50%     3.295000   3.040000   3.810000   1.700000   2.350000   -0.356000   
75%     4.000000   3.367500   3.977500   2.262500   2.727500   -0.224500   
max     4.630000   3.690000   4.790000   2.890000   2.920000    0.074000   

       coeff2_ipc  
count   22.000000  
mean     3.806909  
std      0.804792  
min      2.094000  
25%      3.164000  
50%      3.915000  
75%      4.325750  
max      5.035000

#### Defining groups of data for **ipc** at steps of 25% each

In [ ]:
varmax = df_ipc['coeff1_ipc'].max()
varmin = df_ipc['coeff1_ipc'].min()
var025=stat_ipc.iloc[4,5]
var050=stat_ipc.iloc[5,5]
var075=stat_ipc.iloc[6,5]
var100=stat_ipc.iloc[7,5]
ipcav = [var025, var050, var075, var100]
print(ipcav)

[-0.5032500000000003, -0.356, -0.22449999999999998, 0.0739999999999999]


#### IPVN

In [ ]:
# Read data from CSV file
os.listdir(os.getcwd())
df_ipvn = pd.read_csv('ipvn2021.csv')
df_ipvn.head()

Department          City      2017       2018       2019      2020  \
0     Antioquia      Medellín  8.506465   9.121538  10.204082  7.810578   
1     Atlántico  Barranquilla  6.576834   4.010718   3.807760  4.893370   
2  Bogotá, D.C.  Bogotá, D.C.  7.987103   5.323324  10.829418  4.962362   
3       Bolívar     Cartagena  9.435788   1.291121   6.251091 -2.547247   
4        Caldas     Manizales  8.665148  11.462351   8.395396  6.606982   

       2021  
0  3.987326  
1  0.878900  
2  2.233460  
3  5.100898  
4  5.275626

#### Data Preparation

In [ ]:
mun=df_ipvn['City']+', '+df_ipvn['Department']
mun = pd.DataFrame(mun, columns=['Location'])

df_ipvn[['Location']] = mun[['Location']]
df_ipvn.drop(['Department', 'City'], axis=1, inplace=True)
df_ipvn

2017       2018       2019       2020      2021  \
0    8.506465   9.121538  10.204082   7.810578  3.987326   
1    6.576834   4.010718   3.807760   4.893370  0.878900   
2    7.987103   5.323324  10.829418   4.962362  2.233460   
3    9.435788   1.291121   6.251091  -2.547247  5.100898   
4    8.665148  11.462351   8.395396   6.606982  5.275626   
5   11.724255  10.433131  11.181449   5.582374  9.491640   
6    2.092690   2.648821  -0.346494   0.274499  2.901254   
7   -4.299694  -4.017765  26.998816  -0.177936  1.640918   
8   12.734119  24.826582   6.256861   3.170196  8.675268   
9    9.814119   8.156464  -5.027571   4.900956  7.870300   
10  11.489012   4.743600   8.698368   5.646146  5.150145   
11  14.055689  13.165900  13.205597   8.261796 -1.788422   
12   3.572068   4.209525  -0.149303   1.810932  2.086107   
13  10.740127   4.817760   8.899737   1.220690  1.296003   
14  10.195933  11.628887  11.617725  10.219126  1.644724   

                      Location  
0          Medellín, Antioquia  
1      Barranquilla, Atlántico  
2   Bogotá, D.C., Bogotá, D.C.  
3           Cartagena, Bolívar  
4            Manizales, Caldas  
5               Popayán, Cauca  
6                 Neiva, Huila  
7          Villavicencio, Meta  
8                Pasto, Nariño  
9   Cúcuta, Norte de Santander  
10            Armenia, Quindío  
11          Pereira, Risaralda  
12      Bucaramanga, Santander  
13              Ibagué, Tolima  
14       Cali, Valle del Cauca

In [ ]:
df = df_ipvn
if(df.index.name != 'Location'):
    df = df.set_index('Location')

df_t=df.transpose()
df_t

Location  Medellín, Antioquia  Barranquilla, Atlántico  \
2017                 8.506465                 6.576834   
2018                 9.121538                 4.010718   
2019                10.204082                 3.807760   
2020                 7.810578                 4.893370   
2021                 3.987326                 0.878900   

Location  Bogotá, D.C., Bogotá, D.C.  Cartagena, Bolívar  Manizales, Caldas  \
2017                        7.987103            9.435788           8.665148   
2018                        5.323324            1.291121          11.462351   
2019                       10.829418            6.251091           8.395396   
2020                        4.962362           -2.547247           6.606982   
2021                        2.233460            5.100898           5.275626   

Location  Popayán, Cauca  Neiva, Huila  Villavicencio, Meta  Pasto, Nariño  \
2017           11.724255      2.092690            -4.299694      12.734119   
2018           10.433131      2.648821            -4.017765      24.826582   
2019           11.181449     -0.346494            26.998816       6.256861   
2020            5.582374      0.274499            -0.177936       3.170196   
2021            9.491640      2.901254             1.640918       8.675268   

Location  Cúcuta, Norte de Santander  Armenia, Quindío  Pereira, Risaralda  \
2017                        9.814119         11.489012           14.055689   
2018                        8.156464          4.743600           13.165900   
2019                       -5.027571          8.698368           13.205597   
2020                        4.900956          5.646146            8.261796   
2021                        7.870300          5.150145           -1.788422   

Location  Bucaramanga, Santander  Ibagué, Tolima  Cali, Valle del Cauca  
2017                    3.572068       10.740127              10.195933  
2018                    4.209525        4.817760              11.628887  
2019                   -0.149303        8.899737              11.617725  
2020                    1.810932        1.220690              10.219126  
2021                    2.086107        1.296003               1.644724

#### An ipvn annual variation trend is estimated for each city

In [ ]:
numberYears = len(df_t)
n = np.linspace(1,numberYears,numberYears)
y=df_t
z = np.polyfit(n,y,1).transpose()
df = pd.DataFrame(z, columns=['coeff1_ipvn', 'coeff2_ipvn'])
df

coeff1_ipvn  coeff2_ipvn
0     -1.034924    11.030769
1     -1.051322     7.187481
2     -1.186825     9.827608
3     -1.250815     7.658775
4     -1.163441    11.571425
5     -0.931599    12.477366
6     -0.075719     1.741312
7      1.572105    -0.687448
8     -2.977409    20.064831
9     -0.714315     7.285798
10    -1.177519    10.678011
11    -3.659233    20.357810
12    -0.537052     3.917020
13    -2.248532    12.140459
14    -1.851218    14.614932

In [ ]:
frames = [df_ipvn, df]
df_ipvn = pd.concat(frames, axis=1, join='inner')

if(df_ipvn.index.name != 'Location'):
    df_ipvn = df_ipvn.set_index('Location')

df_ipvn

2017       2018       2019       2020  \
Location                                                                 
Medellín, Antioquia          8.506465   9.121538  10.204082   7.810578   
Barranquilla, Atlántico      6.576834   4.010718   3.807760   4.893370   
Bogotá, D.C., Bogotá, D.C.   7.987103   5.323324  10.829418   4.962362   
Cartagena, Bolívar           9.435788   1.291121   6.251091  -2.547247   
Manizales, Caldas            8.665148  11.462351   8.395396   6.606982   
Popayán, Cauca              11.724255  10.433131  11.181449   5.582374   
Neiva, Huila                 2.092690   2.648821  -0.346494   0.274499   
Villavicencio, Meta         -4.299694  -4.017765  26.998816  -0.177936   
Pasto, Nariño               12.734119  24.826582   6.256861   3.170196   
Cúcuta, Norte de Santander   9.814119   8.156464  -5.027571   4.900956   
Armenia, Quindío            11.489012   4.743600   8.698368   5.646146   
Pereira, Risaralda          14.055689  13.165900  13.205597   8.261796   
Bucaramanga, Santander       3.572068   4.209525  -0.149303   1.810932   
Ibagué, Tolima              10.740127   4.817760   8.899737   1.220690   
Cali, Valle del Cauca       10.195933  11.628887  11.617725  10.219126   

                                2021  coeff1_ipvn  coeff2_ipvn  
Location                                                        
Medellín, Antioquia         3.987326    -1.034924    11.030769  
Barranquilla, Atlántico     0.878900    -1.051322     7.187481  
Bogotá, D.C., Bogotá, D.C.  2.233460    -1.186825     9.827608  
Cartagena, Bolívar          5.100898    -1.250815     7.658775  
Manizales, Caldas           5.275626    -1.163441    11.571425  
Popayán, Cauca              9.491640    -0.931599    12.477366  
Neiva, Huila                2.901254    -0.075719     1.741312  
Villavicencio, Meta         1.640918     1.572105    -0.687448  
Pasto, Nariño               8.675268    -2.977409    20.064831  
Cúcuta, Norte de Santander  7.870300    -0.714315     7.285798  
Armenia, Quindío            5.150145    -1.177519    10.678011  
Pereira, Risaralda         -1.788422    -3.659233    20.357810  
Bucaramanga, Santander      2.086107    -0.537052     3.917020  
Ibagué, Tolima              1.296003    -2.248532    12.140459  
Cali, Valle del Cauca       1.644724    -1.851218    14.614932

In [ ]:
stat_ipvn=df_ipvn.describe()
stat_ipvn

2017       2018       2019       2020       2021  coeff1_ipvn  \
count  15.000000  15.000000  15.000000  15.000000  15.000000    15.000000   
mean    8.219310   7.454797   8.054862   4.175655   3.762943    -1.219188   
std     4.710155   6.622306   7.343606   3.513751   3.162017     1.209337   
min    -4.299694  -4.017765  -5.027571  -2.547247  -1.788422    -3.659233   
25%     7.281968   4.110122   5.029426   1.515811   1.642821    -1.551016   
50%     9.435788   5.323324   8.698368   4.900956   2.901254    -1.163441   
75%    11.114570  10.947741  11.005434   6.126564   5.212885    -0.822957   
max    14.055689  24.826582  26.998816  10.219126   9.491640     1.572105   

       coeff2_ipvn  
count    15.000000  
mean      9.991077  
std       5.884667  
min      -0.687448  
25%       7.236639  
50%      10.678011  
75%      12.308912  
max      20.357810

#### Defining groups of data for **ipvn** at steps of 25% each

In [ ]:
varmax = df_ipvn['coeff1_ipvn'].max()
varmin = df_ipvn['coeff1_ipvn'].min()
var025=stat_ipvn.iloc[4,5]
var050=stat_ipvn.iloc[5,5]
var075=stat_ipvn.iloc[6,5]
var100=stat_ipvn.iloc[7,5]
ipvnav = [var025, var050, var075, var100]
print(ipvnav)

[-1.5510163507500003, -1.1634413678, -0.8229566710000005, 1.5721051309999998]


#### Preparing dataframe with geographical coordinates for analysis

In [ ]:
df_census=census

# Setting dataframe index as Location
if(df_census.index.name != 'Location'):
    df_census = df_census.set_index('Location')
df_census=df_census[['latitude', 'longitude']]

df_census

latitude  longitude
Location                                    
Medellín, Antioquia      6.244338 -75.573553
Abejorral, Antioquia     5.804950 -75.429842
Abriaquí, Antioquia      6.628479 -76.083270
Alejandría, Antioquia    6.355780 -75.098662
Amagá, Antioquia         6.035817 -75.700911
...                           ...        ...
Caruru, Vaupés           1.015525 -71.296148
Taraira, Vaupés         -0.687501 -69.598422
Puerto Carreño, Vichada  6.187971 -67.489467
Santa Rosalía, Vichada   5.141291 -70.857403
Cumaribo, Vichada        4.447150 -69.797584

[1084 rows x 2 columns]

Consolidate one table with variation rates of ICCV, IPC, and IPVN

In [ ]:
frames = [df_iccv, df_ipc, df_ipvn, df_census]
df_const = pd.concat(frames, axis=1, join='inner')
df_const.drop(['2017', '2018', '2019', '2020', '2021'], axis=1, inplace=True)
df_const

coeff1_iccv  coeff2_iccv  coeff1_ipc  coeff2_ipc  \
Location                                                                       
Medellín, Antioquia               0.252        3.724      -0.545       5.017   
Barranquilla, Atlántico           0.853        0.835      -0.221       3.895   
Bogotá, D.C., Bogotá, D.C.        0.058        2.850      -0.725       5.035   
Cartagena, Bolívar                0.825        0.625      -0.534       4.182   
Manizales, Caldas                 0.387        3.527      -0.468       4.620   
Popayán, Cauca                    0.983        0.715      -0.252       3.942   
Neiva, Huila                      1.345       -0.369      -0.203       3.039   
Pasto, Nariño                     0.335        3.389      -0.580       4.652   
Cúcuta, Norte de Santander        0.569        1.181      -0.016       3.094   
Armenia, Quindío                  0.429        3.385      -0.235       3.935   
Pereira, Risaralda                0.646        2.910      -0.390       4.336   
Bucaramanga, Santander            1.235        0.317      -0.381       3.967   
Ibagué, Tolima                    0.687        0.823      -0.366       3.498   
Cali, Valle del Cauca             0.171        3.901      -0.551       4.829   

                            coeff1_ipvn  coeff2_ipvn   latitude  longitude  
Location                                                                    
Medellín, Antioquia           -1.034924    11.030769   6.244338 -75.573553  
Barranquilla, Atlántico       -1.051322     7.187481  10.979967 -74.801309  
Bogotá, D.C., Bogotá, D.C.    -1.186825     9.827608   4.672662 -74.058174  
Cartagena, Bolívar            -1.250815     7.658775  10.419584 -75.527122  
Manizales, Caldas             -1.163441    11.571425   5.066891 -75.506666  
Popayán, Cauca                -0.931599    12.477366   2.442229 -76.607237  
Neiva, Huila                  -0.075719     1.741312   2.926313 -75.289173  
Pasto, Nariño                 -2.977409    20.064831   1.214601 -77.278276  
Cúcuta, Norte de Santander    -0.714315     7.285798   7.897146 -72.508039  
Armenia, Quindío              -1.177519    10.678011   4.536307 -75.672375  
Pereira, Risaralda            -3.659233    20.357810   4.814261 -75.694678  
Bucaramanga, Santander        -0.537052     3.917020   7.111461 -73.117287  
Ibagué, Tolima                -2.248532    12.140459   4.444660 -75.243001  
Cali, Valle del Cauca         -1.851218    14.614932   3.451792 -76.532494

In [ ]:
df_const.describe()

coeff1_iccv  coeff2_iccv  coeff1_ipc  coeff2_ipc  coeff1_ipvn  \
count    14.000000    14.000000    14.00000   14.000000    14.000000   
mean      0.626786     1.986643    -0.39050    4.145786    -1.418566   
std       0.388678     1.511829     0.19059    0.648477     0.965844   
min       0.058000    -0.369000    -0.72500    3.039000    -3.659233   
25%       0.348000     0.742000    -0.54225    3.905000    -1.701117   
50%       0.607500     2.015500    -0.38550    4.074500    -1.170480   
75%       0.846000     3.388000    -0.23925    4.644000    -0.957430   
max       1.345000     3.901000    -0.01600    5.035000    -0.075719   

       coeff2_ipvn   latitude  longitude  
count    14.000000  14.000000  14.000000  
mean     10.753828   5.444444 -75.243527  
std       5.281567   2.842056   1.298338  
min       1.741312   1.214601 -77.278276  
25%       7.379042   3.700009 -75.689102  
50%      10.854390   4.743461 -75.516894  
75%      12.393139   6.894680 -74.911732  
max      20.357810  10.979967 -72.508039

#### Creating folium map for ICCV annual variation

In [ ]:
# create map of iccv annual variation using latitude and longitude values
map = folium.Map(location=[latitude, longitude], zoom_start=5)

# add markers "Municipalities" to map
for label, lat, lng, var in zip(df_const.index, df_const['latitude'], df_const['longitude'], df_const['coeff1_iccv']):
    label = '{}, {:.2f}'.format(label, var) 
    label = folium.Popup(label, parse_html=True)
    
    if var<=iccvav[0]:
        color='red'
        radius=6
        fill=False
    elif var<=iccvav[1]:
        color='grey'
        radius=6
        fill=False        
    elif var<=iccvav[2]:
        color='orange'
        radius=6
        fill=False        
    elif var<=iccvav[3]:
        color='cyan'
        radius=6
        fill=False        
    else: 
        color='yellow'    
    
    folium.CircleMarker(
        [lat, lng],
        radius=radius,
        popup=label,
        color=color,
        fill=fill,
        fill_color=color,
        fill_opacity=0.7,
        parse_html=False).add_to(map)

map

#### Creating folium map for IPC annual variation

In [ ]:
# create map of iccv annual variation using latitude and longitude values
map = folium.Map(location=[latitude, longitude], zoom_start=5)

# add markers "Municipalities" to map
for label, lat, lng, var in zip(df_const.index, df_const['latitude'], df_const['longitude'], df_const['coeff1_ipc']):
    label = '{}, {:.2f}'.format(label, var) 
    label = folium.Popup(label, parse_html=True)
    
    if var<=ipcav[0]:
        color='red'
        radius=6
        fill=False
    elif var<=ipcav[1]:
        color='grey'
        radius=6
        fill=False        
    elif var<=ipcav[2]:
        color='orange'
        radius=6
        fill=False        
    elif var<=ipcav[3]:
        color='cyan'
        radius=6
        fill=False        
    else: 
        color='yellow'    
    
    folium.CircleMarker(
        [lat, lng],
        radius=radius,
        popup=label,
        color=color,
        fill=fill,
        fill_color=color,
        fill_opacity=0.7,
        parse_html=False).add_to(map)

map

#### Creating folium map for IPVN annual variation

In [ ]:
# create map of iccv annual variation using latitude and longitude values
map = folium.Map(location=[latitude, longitude], zoom_start=5)

# add markers "Municipalities" to map
for label, lat, lng, var in zip(df_const.index, df_const['latitude'], df_const['longitude'], df_const['coeff1_ipvn']):
    label = '{}, {:.2f}'.format(label, var) 
    label = folium.Popup(label, parse_html=True)
    
    if var<=ipvnav[0]:
        color='red'
        radius=6
        fill=False
    elif var<=ipvnav[1]:
        color='grey'
        radius=6
        fill=False        
    elif var<=ipvnav[2]:
        color='orange'
        radius=6
        fill=False        
    elif var<=ipvnav[3]:
        color='cyan'
        radius=6
        fill=False        
    else: 
        color='yellow'    
    
    folium.CircleMarker(
        [lat, lng],
        radius=radius,
        popup=label,
        color=color,
        fill=fill,
        fill_color=color,
        fill_opacity=0.7,
        parse_html=False).add_to(map)

map

#### Conclusion: National Economic Sector georeferenced analysis

There is evidence of annual variation in construction costs above the IPC, in the entire range of percentiles; the cities of the coffee region, where Supía is located, show a similar behavior, in this variation. However, Armenia presents a greater variation in the IPC, and Pereira a lower variation in the price of new housing. The IPVN shows a smaller variation with respect to the IPC, an exception of some cities that are in the last percentile rank.

---

### 3. Market Analysis
National real-state market georeferenced analysis; in this section the variables **annual sales variation**, **annual new home launches projects variation**, and **annual offer housing variation** is evaluated.
#### Download and Explore Dataset Real-State Market

Downloading real-state market dataset got from surveys to sales projects in order to asses the **offer**, **demand** and **inventory rotation**.


####  Annual Sales Variation (year-to-date sales)

Total housing units sales annual variation, VIS( Social Housing) unit sales annual variation, and NO-VIS unit sales annual variation is taken in consideration for the georeferenced analysis.

In [ ]:
# Read data from CSV file
os.listdir(os.getcwd())
df_asv = pd.read_csv('sales.csv')
df_asv.head()

Department          City  Total Unit Var.  VIS Var.  No-VIS Var.
0     Antioquia      Medellín             0.08      0.07         0.10
1     Atlántico  Barranquilla             0.20      0.19         0.25
2  Bogotá, D.C.  Bogotá, D.C.             0.12      0.22        -0.13
3       Bolívar     Cartagena            -0.16     -0.23         0.02
4        Caldas     Manizales             0.12      0.07         0.17

#### Data Preparation

In [ ]:
mun=df_asv['City']+', '+df_asv['Department']
mun = pd.DataFrame(mun, columns=['Location'])

df_asv[['Location']] = mun[['Location']]
df_asv.drop(['Department', 'City'], axis=1, inplace=True)
df_asv

Total Unit Var.  VIS Var.  No-VIS Var.                    Location
0              0.08      0.07         0.10         Medellín, Antioquia
1              0.20      0.19         0.25     Barranquilla, Atlántico
2              0.12      0.22        -0.13  Bogotá, D.C., Bogotá, D.C.
3             -0.16     -0.23         0.02          Cartagena, Bolívar
4              0.12      0.07         0.17           Manizales, Caldas
5             -0.14     -0.17        -0.09           Montería, Córdoba
6              0.13      0.70        -0.22      Santa Marta, Magdalena
7              0.03     -0.04         0.19         Villavicencio, Meta
8             -0.01     -0.12         0.28  Cúcuta, Norte de Santander
9              0.02     -0.07         0.20            Armenia, Quindío
10             0.07      0.11         0.00          Pereira, Risaralda
11            -0.01      0.01        -0.03      Bucaramanga, Santander
12             0.09      0.14        -0.07              Ibagué, Tolima
13             0.32      0.32         0.30       Cali, Valle del Cauca

In [ ]:
if(df_asv.index.name != 'Location'):
    df_asv = df_asv.set_index('Location')

df_asv

Total Unit Var.  VIS Var.  No-VIS Var.
Location                                                          
Medellín, Antioquia                    0.08      0.07         0.10
Barranquilla, Atlántico                0.20      0.19         0.25
Bogotá, D.C., Bogotá, D.C.             0.12      0.22        -0.13
Cartagena, Bolívar                    -0.16     -0.23         0.02
Manizales, Caldas                      0.12      0.07         0.17
Montería, Córdoba                     -0.14     -0.17        -0.09
Santa Marta, Magdalena                 0.13      0.70        -0.22
Villavicencio, Meta                    0.03     -0.04         0.19
Cúcuta, Norte de Santander            -0.01     -0.12         0.28
Armenia, Quindío                       0.02     -0.07         0.20
Pereira, Risaralda                     0.07      0.11         0.00
Bucaramanga, Santander                -0.01      0.01        -0.03
Ibagué, Tolima                         0.09      0.14        -0.07
Cali, Valle del Cauca                  0.32      0.32         0.30

In [ ]:
stat_asv=df_asv.describe()
stat_asv

Total Unit Var.   VIS Var.  No-VIS Var.
count        14.000000  14.000000    14.000000
mean          0.061429   0.085714     0.069286
std           0.124459   0.235068     0.166015
min          -0.160000  -0.230000    -0.220000
25%          -0.002500  -0.062500    -0.060000
50%           0.075000   0.070000     0.060000
75%           0.120000   0.177500     0.197500
max           0.320000   0.700000     0.300000

#### Defining groups of data for **annual sales variation** at steps of 25% each

In [ ]:
var025=stat_asv.iloc[4,0]
var050=stat_asv.iloc[5,0]
var075=stat_asv.iloc[6,0]
var100=stat_asv.iloc[7,0]
asv_t = [var025, var050, var075, var100]
print(asv_t)

[-0.0025000000000000005, 0.07500000000000001, 0.12, 0.32]


In [ ]:
var025=stat_asv.iloc[4,1]
var050=stat_asv.iloc[5,1]
var075=stat_asv.iloc[6,1]
var100=stat_asv.iloc[7,1]
asv_vis = [var025, var050, var075, var100]
print(asv_vis)

[-0.0625, 0.07, 0.1775, 0.7]


In [ ]:
var025=stat_asv.iloc[4,2]
var050=stat_asv.iloc[5,2]
var075=stat_asv.iloc[6,2]
var100=stat_asv.iloc[7,2]
asv_nvis = [var025, var050, var075, var100]
print(asv_nvis)

[-0.060000000000000005, 0.060000000000000005, 0.1975, 0.3]


Consolidate one table with annual sales variation rates

In [ ]:
frames = [df_asv, df_census]
df_asv = pd.concat(frames, axis=1, join='inner')
df_asv

Total Unit Var.  VIS Var.  No-VIS Var.   latitude  \
Location                                                                        
Medellín, Antioquia                    0.08      0.07         0.10   6.244338   
Barranquilla, Atlántico                0.20      0.19         0.25  10.979967   
Bogotá, D.C., Bogotá, D.C.             0.12      0.22        -0.13   4.672662   
Cartagena, Bolívar                    -0.16     -0.23         0.02  10.419584   
Manizales, Caldas                      0.12      0.07         0.17   5.066891   
Montería, Córdoba                     -0.14     -0.17        -0.09   8.604605   
Santa Marta, Magdalena                 0.13      0.70        -0.22  11.242229   
Villavicencio, Meta                    0.03     -0.04         0.19   4.131511   
Cúcuta, Norte de Santander            -0.01     -0.12         0.28   7.897146   
Armenia, Quindío                       0.02     -0.07         0.20   4.536307   
Pereira, Risaralda                     0.07      0.11         0.00   4.814261   
Bucaramanga, Santander                -0.01      0.01        -0.03   7.111461   
Ibagué, Tolima                         0.09      0.14        -0.07   4.444660   
Cali, Valle del Cauca                  0.32      0.32         0.30   3.451792   

                            longitude  
Location                               
Medellín, Antioquia        -75.573553  
Barranquilla, Atlántico    -74.801309  
Bogotá, D.C., Bogotá, D.C. -74.058174  
Cartagena, Bolívar         -75.527122  
Manizales, Caldas          -75.506666  
Montería, Córdoba          -75.978320  
Santa Marta, Magdalena     -74.205561  
Villavicencio, Meta        -73.620667  
Cúcuta, Norte de Santander -72.508039  
Armenia, Quindío           -75.672375  
Pereira, Risaralda         -75.694678  
Bucaramanga, Santander     -73.117287  
Ibagué, Tolima             -75.243001  
Cali, Valle del Cauca      -76.532494

#### Creating folium map for total annual sales variation

In [ ]:
# create map of iccv annual variation using latitude and longitude values
map = folium.Map(location=[latitude, longitude], zoom_start=5)

# add markers "Municipalities" to map
for label, lat, lng, var in zip(df_asv.index, df_asv['latitude'], df_asv['longitude'], df_asv['Total Unit Var.']):
    label = '{}, {:.2f}'.format(label, var) 
    label = folium.Popup(label, parse_html=True)
    
    if var<=asv_t[0]:
        color='red'
        radius=6
        fill=False
    elif var<=asv_t[1]:
        color='grey'
        radius=6
        fill=False        
    elif var<=asv_t[2]:
        color='orange'
        radius=6
        fill=False        
    elif var<=asv_t[3]:
        color='cyan'
        radius=6
        fill=False        
    else: 
        color='yellow'    
    
    folium.CircleMarker(
        [lat, lng],
        radius=radius,
        popup=label,
        color=color,
        fill=fill,
        fill_color=color,
        fill_opacity=0.7,
        parse_html=False).add_to(map)

map

#### Creating folium map for VIS annual sales variation

In [ ]:
# create map of iccv annual variation using latitude and longitude values
map = folium.Map(location=[latitude, longitude], zoom_start=5)

# add markers "Municipalities" to map
for label, lat, lng, var in zip(df_asv.index, df_asv['latitude'], df_asv['longitude'], df_asv['VIS Var.']):
    label = '{}, {:.2f}'.format(label, var) 
    label = folium.Popup(label, parse_html=True)
    
    if var<=asv_vis[0]:
        color='red'
        radius=6
        fill=False
    elif var<=asv_vis[1]:
        color='grey'
        radius=6
        fill=False        
    elif var<=asv_vis[2]:
        color='orange'
        radius=6
        fill=False        
    elif var<=asv_vis[3]:
        color='cyan'
        radius=6
        fill=False        
    else: 
        color='yellow'    
    
    folium.CircleMarker(
        [lat, lng],
        radius=radius,
        popup=label,
        color=color,
        fill=fill,
        fill_color=color,
        fill_opacity=0.7,
        parse_html=False).add_to(map)

map

#### Creating folium map for NO-VIS annual sales variation

In [ ]:
# create map of iccv annual variation using latitude and longitude values
map = folium.Map(location=[latitude, longitude], zoom_start=5)

# add markers "Municipalities" to map
for label, lat, lng, var in zip(df_asv.index, df_asv['latitude'], df_asv['longitude'], df_asv['No-VIS Var.']):
    label = '{}, {:.2f}'.format(label, var) 
    label = folium.Popup(label, parse_html=True)
    
    if var<=asv_nvis[0]:
        color='red'
        radius=6
        fill=False
    elif var<=asv_nvis[1]:
        color='grey'
        radius=6
        fill=False        
    elif var<=asv_nvis[2]:
        color='orange'
        radius=6
        fill=False        
    elif var<=asv_nvis[3]:
        color='cyan'
        radius=6
        fill=False        
    else: 
        color='yellow'    
    
    folium.CircleMarker(
        [lat, lng],
        radius=radius,
        popup=label,
        color=color,
        fill=fill,
        fill_color=color,
        fill_opacity=0.7,
        parse_html=False).add_to(map)

map

#### Conclusion: annual sales georeferenced analysis

There is a high annual variation in the sales of real estate units, especially in the cities of Cali, Barranquilla and Santa Marta, with increases of up to 32%. Manizales, the capital city of the region where Supía is located, is in the next percentile, with a variation in the range up to 12%, along with the capital city Bogotá and Medellín. The considerable increase in sales in the VIS segment stands out, with variations up to 70%. However, the Manizales region experiences a greater variation in the NO-VIS segment with a variation of 17%.

####   Annual New Home Launches Projects Variation (year-to-date sales)

Total housing units launching annual variation, VIS( Social Housing) unit launching annual variation, and NO-VIS unit launching annual variation is taken in consideration for the georeferenced analysis.

In [ ]:
# Read data from CSV file
os.listdir(os.getcwd())
df_alv = pd.read_csv('launching.csv')
df_alv.head()

Department          City  Total Unit Var.  VIS Var.  No-VIS Var.
0     Antioquia      Medellín            -0.30     -0.28        -0.31
1     Atlántico  Barranquilla             0.05      0.08        -0.19
2  Bogotá, D.C.  Bogotá, D.C.             0.20      0.41        -0.28
3       Bolívar     Cartagena            -0.25     -0.28        -0.20
4        Caldas     Manizales            -0.42     -0.43        -0.40

#### Data Preparation

In [ ]:
mun=df_alv['City']+', '+df_alv['Department']
mun = pd.DataFrame(mun, columns=['Location'])

df_alv[['Location']] = mun[['Location']]
df_alv.drop(['Department', 'City'], axis=1, inplace=True)
df_alv

Total Unit Var.  VIS Var.  No-VIS Var.                    Location
0             -0.30     -0.28        -0.31         Medellín, Antioquia
1              0.05      0.08        -0.19     Barranquilla, Atlántico
2              0.20      0.41        -0.28  Bogotá, D.C., Bogotá, D.C.
3             -0.25     -0.28        -0.20          Cartagena, Bolívar
4             -0.42     -0.43        -0.40           Manizales, Caldas
5             -0.44     -0.58         1.83           Montería, Córdoba
6              0.17      0.20         0.12      Santa Marta, Magdalena
7             -0.90     -1.09        -0.51         Villavicencio, Meta
8             -0.38     -0.34        -0.51  Cúcuta, Norte de Santander
9             -0.17      0.26        -0.63            Armenia, Quindío
10            -0.14     -0.21         0.08          Pereira, Risaralda
11             0.25      0.18         0.43      Bucaramanga, Santander
12            -0.07      0.19        -0.83              Ibagué, Tolima
13             0.36      0.31         0.71       Cali, Valle del Cauca

In [ ]:
if(df_alv.index.name != 'Location'):
    df_alv = df_alv.set_index('Location')

df_alv

Total Unit Var.  VIS Var.  No-VIS Var.
Location                                                          
Medellín, Antioquia                   -0.30     -0.28        -0.31
Barranquilla, Atlántico                0.05      0.08        -0.19
Bogotá, D.C., Bogotá, D.C.             0.20      0.41        -0.28
Cartagena, Bolívar                    -0.25     -0.28        -0.20
Manizales, Caldas                     -0.42     -0.43        -0.40
Montería, Córdoba                     -0.44     -0.58         1.83
Santa Marta, Magdalena                 0.17      0.20         0.12
Villavicencio, Meta                   -0.90     -1.09        -0.51
Cúcuta, Norte de Santander            -0.38     -0.34        -0.51
Armenia, Quindío                      -0.17      0.26        -0.63
Pereira, Risaralda                    -0.14     -0.21         0.08
Bucaramanga, Santander                 0.25      0.18         0.43
Ibagué, Tolima                        -0.07      0.19        -0.83
Cali, Valle del Cauca                  0.36      0.31         0.71

In [ ]:
stat_alv=df_alv.describe()
stat_alv

Total Unit Var.   VIS Var.  No-VIS Var.
count        14.000000  14.000000    14.000000
mean         -0.145714  -0.112857    -0.049286
std           0.339291   0.420099     0.681700
min          -0.900000  -1.090000    -0.830000
25%          -0.360000  -0.325000    -0.482500
50%          -0.155000  -0.065000    -0.240000
75%           0.140000   0.197500     0.110000
max           0.360000   0.410000     1.830000

#### Defining groups of data for **annual launching projects variation** at steps of 25% each

In [ ]:
var025=stat_alv.iloc[4,0]
var050=stat_alv.iloc[5,0]
var075=stat_alv.iloc[6,0]
var100=stat_alv.iloc[7,0]
alv_t = [var025, var050, var075, var100]
print(alv_t)

[-0.36, -0.15500000000000003, 0.14, 0.36]


In [ ]:
var025=stat_alv.iloc[4,1]
var050=stat_alv.iloc[5,1]
var075=stat_alv.iloc[6,1]
var100=stat_alv.iloc[7,1]
alv_vis = [var025, var050, var075, var100]
print(alv_vis)

[-0.325, -0.06499999999999999, 0.1975, 0.41]


In [ ]:
var025=stat_alv.iloc[4,2]
var050=stat_alv.iloc[5,2]
var075=stat_alv.iloc[6,2]
var100=stat_alv.iloc[7,2]
alv_nvis = [var025, var050, var075, var100]
print(alv_nvis)

[-0.48250000000000004, -0.24000000000000002, 0.11, 1.83]


Consolidate one table with annual launching variation rates

In [ ]:
frames = [df_alv, df_census]
df_alv = pd.concat(frames, axis=1, join='inner')
df_alv

Total Unit Var.  VIS Var.  No-VIS Var.   latitude  \
Location                                                                        
Medellín, Antioquia                   -0.30     -0.28        -0.31   6.244338   
Barranquilla, Atlántico                0.05      0.08        -0.19  10.979967   
Bogotá, D.C., Bogotá, D.C.             0.20      0.41        -0.28   4.672662   
Cartagena, Bolívar                    -0.25     -0.28        -0.20  10.419584   
Manizales, Caldas                     -0.42     -0.43        -0.40   5.066891   
Montería, Córdoba                     -0.44     -0.58         1.83   8.604605   
Santa Marta, Magdalena                 0.17      0.20         0.12  11.242229   
Villavicencio, Meta                   -0.90     -1.09        -0.51   4.131511   
Cúcuta, Norte de Santander            -0.38     -0.34        -0.51   7.897146   
Armenia, Quindío                      -0.17      0.26        -0.63   4.536307   
Pereira, Risaralda                    -0.14     -0.21         0.08   4.814261   
Bucaramanga, Santander                 0.25      0.18         0.43   7.111461   
Ibagué, Tolima                        -0.07      0.19        -0.83   4.444660   
Cali, Valle del Cauca                  0.36      0.31         0.71   3.451792   

                            longitude  
Location                               
Medellín, Antioquia        -75.573553  
Barranquilla, Atlántico    -74.801309  
Bogotá, D.C., Bogotá, D.C. -74.058174  
Cartagena, Bolívar         -75.527122  
Manizales, Caldas          -75.506666  
Montería, Córdoba          -75.978320  
Santa Marta, Magdalena     -74.205561  
Villavicencio, Meta        -73.620667  
Cúcuta, Norte de Santander -72.508039  
Armenia, Quindío           -75.672375  
Pereira, Risaralda         -75.694678  
Bucaramanga, Santander     -73.117287  
Ibagué, Tolima             -75.243001  
Cali, Valle del Cauca      -76.532494

#### Creating folium map for total annual launching housing variation

In [ ]:
# create map of iccv annual variation using latitude and longitude values
map = folium.Map(location=[latitude, longitude], zoom_start=5)

# add markers "Municipalities" to map
for label, lat, lng, var in zip(df_alv.index, df_alv['latitude'], df_alv['longitude'], df_alv['Total Unit Var.']):
    label = '{}, {:.2f}'.format(label, var) 
    label = folium.Popup(label, parse_html=True)
    
    if var<=alv_t[0]:
        color='red'
        radius=6
        fill=False
    elif var<=alv_t[1]:
        color='grey'
        radius=6
        fill=False        
    elif var<=alv_t[2]:
        color='orange'
        radius=6
        fill=False        
    elif var<=alv_t[3]:
        color='cyan'
        radius=6
        fill=False        
    else: 
        color='yellow'    
    
    folium.CircleMarker(
        [lat, lng],
        radius=radius,
        popup=label,
        color=color,
        fill=fill,
        fill_color=color,
        fill_opacity=0.7,
        parse_html=False).add_to(map)

map

#### Creating folium map for VIS annual launching housing variation

In [ ]:
# create map of iccv annual variation using latitude and longitude values
map = folium.Map(location=[latitude, longitude], zoom_start=5)

# add markers "Municipalities" to map
for label, lat, lng, var in zip(df_alv.index, df_alv['latitude'], df_alv['longitude'], df_alv['VIS Var.']):
    label = '{}, {:.2f}'.format(label, var) 
    label = folium.Popup(label, parse_html=True)
    
    if var<=alv_vis[0]:
        color='red'
        radius=6
        fill=False
    elif var<=alv_vis[1]:
        color='grey'
        radius=6
        fill=False        
    elif var<=alv_vis[2]:
        color='orange'
        radius=6
        fill=False        
    elif var<=alv_vis[3]:
        color='cyan'
        radius=6
        fill=False        
    else: 
        color='yellow'    
    
    folium.CircleMarker(
        [lat, lng],
        radius=radius,
        popup=label,
        color=color,
        fill=fill,
        fill_color=color,
        fill_opacity=0.7,
        parse_html=False).add_to(map)

map

#### Creating folium map for NO-VIS annual launching housing variation

In [ ]:
# create map of iccv annual variation using latitude and longitude values
map = folium.Map(location=[latitude, longitude], zoom_start=5)

# add markers "Municipalities" to map
for label, lat, lng, var in zip(df_alv.index, df_alv['latitude'], df_alv['longitude'], df_alv['VIS Var.']):
    label = '{}, {:.2f}'.format(label, var) 
    label = folium.Popup(label, parse_html=True)
    
    if var<=alv_nvis[0]:
        color='red'
        radius=6
        fill=False
    elif var<=alv_nvis[1]:
        color='grey'
        radius=6
        fill=False        
    elif var<=alv_nvis[2]:
        color='orange'
        radius=6
        fill=False        
    elif var<=alv_nvis[3]:
        color='cyan'
        radius=6
        fill=False        
    else: 
        color='yellow'    
    
    folium.CircleMarker(
        [lat, lng],
        radius=radius,
        popup=label,
        color=color,
        fill=fill,
        fill_color=color,
        fill_opacity=0.7,
        parse_html=False).add_to(map)

map

#### Conclusion: annual launching housing units georeferenced analysis

Regarding the launching of new housing units, the increase in NO-VIS units stands out, with increases of up to 183%, with a large part of the cities analyzed being located in this percentile, including Bogotá, Cali, Santa Marta and Armenia. The Manizales region has presented a drop in the launch of units, more accentuated in VIS housing.

####  Annual Offer Variation (year-to-date offer)

Total housing units offer annual variation, VIS( Social Housing) unit offer annual variation, and NO-VIS unit offer annual variation is taken in consideration for the georeferenced analysis.

In [ ]:
# Read data from CSV file
os.listdir(os.getcwd())
df_aov = pd.read_csv('oferta2021.csv')
df_aov.head()

Department          City  Unit Var.  rot2020 vis  rot2020 no-vis  \
0     Antioquia      Medellín     -0.248          9.5            17.4   
1     Atlántico  Barranquilla     -0.022          6.7            23.8   
2  Bogotá, D.C.  Bogotá, D.C.      0.309          3.0            14.2   
3       Bolívar     Cartagena     -0.074          7.7            25.2   
4        Caldas     Manizales     -0.334          5.2            21.3   

   rot2020 total  rot2021 vis  rot2021 no-vis  rot2021 total  
0           14.1          6.4            10.6            8.8  
1            9.7          5.3            10.5            6.3  
2            6.0          3.8            10.5            5.4  
3           12.6          7.9            12.6            9.9  
4           10.0          4.0            10.1            6.9

#### Data Preparation

In [ ]:
df_aov.describe()

Unit Var.  rot2020 vis  rot2020 no-vis  rot2020 total  rot2021 vis  \
count  14.000000    14.000000        14.00000      14.000000    14.000000   
mean   -0.132286     6.742857        19.00000      10.550000     5.464286   
std     0.199976     2.875016         5.29252       3.428108     2.023176   
min    -0.407000     2.200000        11.10000       3.700000     2.000000   
25%    -0.281750     4.525000        14.87500       9.175000     3.850000   
50%    -0.126000     7.450000        18.45000      10.800000     5.750000   
75%    -0.022250     8.800000        23.80000      12.750000     6.475000   
max     0.309000    11.300000        27.20000      15.600000     9.600000   

       rot2021 no-vis  rot2021 total  
count       14.000000      14.000000  
mean        13.064286       7.985714  
std          5.409906       3.173898  
min          8.700000       3.100000  
25%         10.500000       6.450000  
50%         11.000000       7.250000  
75%         12.500000       8.675000  
max         26.500000      15.600000

The calculation of the varion of the inventory rotation within the last year is estimated.

In [ ]:
mun=df_aov['City']+', '+df_aov['Department']
mun = pd.DataFrame(mun, columns=['Location'])

df_aov[['Location']] = mun[['Location']]
df_aov.drop(['Department', 'City'], axis=1, inplace=True)
df_aov

Unit Var.  rot2020 vis  rot2020 no-vis  rot2020 total  rot2021 vis  \
0      -0.248          9.5            17.4           14.1          6.4   
1      -0.022          6.7            23.8            9.7          5.3   
2       0.309          3.0            14.2            6.0          3.8   
3      -0.074          7.7            25.2           12.6          7.9   
4      -0.334          5.2            21.3           10.0          4.0   
5      -0.178          9.6            27.2           15.6          9.6   
6      -0.023          2.5            11.1            6.3          3.3   
7      -0.407         11.3            15.7           12.8          6.7   
8      -0.354          8.2            24.5           12.6          5.1   
9      -0.283          9.0            19.5           13.8          6.2   
10     -0.278          7.2            12.2            9.0          3.5   
11      0.018          4.3            23.8           11.6          6.5   
12     -0.057          8.0            15.4            9.9          6.2   
13      0.079          2.2            14.7            3.7          2.0   

    rot2021 no-vis  rot2021 total                    Location  
0             10.6            8.8         Medellín, Antioquia  
1             10.5            6.3     Barranquilla, Atlántico  
2             10.5            5.4  Bogotá, D.C., Bogotá, D.C.  
3             12.6            9.9          Cartagena, Bolívar  
4             10.1            6.9           Manizales, Caldas  
5             26.5           15.6           Montería, Córdoba  
6             11.8            7.3      Santa Marta, Magdalena  
7             11.4            7.9         Villavicencio, Meta  
8             12.6            7.2  Cúcuta, Norte de Santander  
9             10.6            8.3            Armenia, Quindío  
10             8.7            5.2          Pereira, Risaralda  
11            24.6           12.9      Bucaramanga, Santander  
12            12.2            7.0              Ibagué, Tolima  
13            10.2            3.1       Cali, Valle del Cauca

In [ ]:
if(df_aov.index.name != 'Location'):
    df_aov = df_aov.set_index('Location')

df_aov

Unit Var.  rot2020 vis  rot2020 no-vis  \
Location                                                             
Medellín, Antioquia            -0.248          9.5            17.4   
Barranquilla, Atlántico        -0.022          6.7            23.8   
Bogotá, D.C., Bogotá, D.C.      0.309          3.0            14.2   
Cartagena, Bolívar             -0.074          7.7            25.2   
Manizales, Caldas              -0.334          5.2            21.3   
Montería, Córdoba              -0.178          9.6            27.2   
Santa Marta, Magdalena         -0.023          2.5            11.1   
Villavicencio, Meta            -0.407         11.3            15.7   
Cúcuta, Norte de Santander     -0.354          8.2            24.5   
Armenia, Quindío               -0.283          9.0            19.5   
Pereira, Risaralda             -0.278          7.2            12.2   
Bucaramanga, Santander          0.018          4.3            23.8   
Ibagué, Tolima                 -0.057          8.0            15.4   
Cali, Valle del Cauca           0.079          2.2            14.7   

                            rot2020 total  rot2021 vis  rot2021 no-vis  \
Location                                                                 
Medellín, Antioquia                  14.1          6.4            10.6   
Barranquilla, Atlántico               9.7          5.3            10.5   
Bogotá, D.C., Bogotá, D.C.            6.0          3.8            10.5   
Cartagena, Bolívar                   12.6          7.9            12.6   
Manizales, Caldas                    10.0          4.0            10.1   
Montería, Córdoba                    15.6          9.6            26.5   
Santa Marta, Magdalena                6.3          3.3            11.8   
Villavicencio, Meta                  12.8          6.7            11.4   
Cúcuta, Norte de Santander           12.6          5.1            12.6   
Armenia, Quindío                     13.8          6.2            10.6   
Pereira, Risaralda                    9.0          3.5             8.7   
Bucaramanga, Santander               11.6          6.5            24.6   
Ibagué, Tolima                        9.9          6.2            12.2   
Cali, Valle del Cauca                 3.7          2.0            10.2   

                            rot2021 total  
Location                                   
Medellín, Antioquia                   8.8  
Barranquilla, Atlántico               6.3  
Bogotá, D.C., Bogotá, D.C.            5.4  
Cartagena, Bolívar                    9.9  
Manizales, Caldas                     6.9  
Montería, Córdoba                    15.6  
Santa Marta, Magdalena                7.3  
Villavicencio, Meta                   7.9  
Cúcuta, Norte de Santander            7.2  
Armenia, Quindío                      8.3  
Pereira, Risaralda                    5.2  
Bucaramanga, Santander               12.9  
Ibagué, Tolima                        7.0  
Cali, Valle del Cauca                 3.1

In [ ]:

df1 = df_aov.apply(lambda x: (x[6]-x[3])/x[3], axis=1)
df1= pd.DataFrame(df1, columns=['rot_tot_var'])
df2 = df_aov.apply(lambda x: (x[5]-x[2])/x[2], axis=1)
df2= pd.DataFrame(df2, columns=['rot_tot_nvis'])
df3 = df_aov.apply(lambda x: (x[4]-x[1])/x[1], axis=1)
df3= pd.DataFrame(df3, columns=['rot_tot_vis'])
frames = [df_aov, df1, df2, df3]
df_aov= pd.concat(frames, axis=1, join='inner')
df_aov

Unit Var.  rot2020 vis  rot2020 no-vis  \
Location                                                             
Medellín, Antioquia            -0.248          9.5            17.4   
Barranquilla, Atlántico        -0.022          6.7            23.8   
Bogotá, D.C., Bogotá, D.C.      0.309          3.0            14.2   
Cartagena, Bolívar             -0.074          7.7            25.2   
Manizales, Caldas              -0.334          5.2            21.3   
Montería, Córdoba              -0.178          9.6            27.2   
Santa Marta, Magdalena         -0.023          2.5            11.1   
Villavicencio, Meta            -0.407         11.3            15.7   
Cúcuta, Norte de Santander     -0.354          8.2            24.5   
Armenia, Quindío               -0.283          9.0            19.5   
Pereira, Risaralda             -0.278          7.2            12.2   
Bucaramanga, Santander          0.018          4.3            23.8   
Ibagué, Tolima                 -0.057          8.0            15.4   
Cali, Valle del Cauca           0.079          2.2            14.7   

                            rot2020 total  rot2021 vis  rot2021 no-vis  \
Location                                                                 
Medellín, Antioquia                  14.1          6.4            10.6   
Barranquilla, Atlántico               9.7          5.3            10.5   
Bogotá, D.C., Bogotá, D.C.            6.0          3.8            10.5   
Cartagena, Bolívar                   12.6          7.9            12.6   
Manizales, Caldas                    10.0          4.0            10.1   
Montería, Córdoba                    15.6          9.6            26.5   
Santa Marta, Magdalena                6.3          3.3            11.8   
Villavicencio, Meta                  12.8          6.7            11.4   
Cúcuta, Norte de Santander           12.6          5.1            12.6   
Armenia, Quindío                     13.8          6.2            10.6   
Pereira, Risaralda                    9.0          3.5             8.7   
Bucaramanga, Santander               11.6          6.5            24.6   
Ibagué, Tolima                        9.9          6.2            12.2   
Cali, Valle del Cauca                 3.7          2.0            10.2   

                            rot2021 total  rot_tot_var  rot_tot_nvis  \
Location                                                               
Medellín, Antioquia                   8.8    -0.375887     -0.390805   
Barranquilla, Atlántico               6.3    -0.350515     -0.558824   
Bogotá, D.C., Bogotá, D.C.            5.4    -0.100000     -0.260563   
Cartagena, Bolívar                    9.9    -0.214286     -0.500000   
Manizales, Caldas                     6.9    -0.310000     -0.525822   
Montería, Córdoba                    15.6     0.000000     -0.025735   
Santa Marta, Magdalena                7.3     0.158730      0.063063   
Villavicencio, Meta                   7.9    -0.382812     -0.273885   
Cúcuta, Norte de Santander            7.2    -0.428571     -0.485714   
Armenia, Quindío                      8.3    -0.398551     -0.456410   
Pereira, Risaralda                    5.2    -0.422222     -0.286885   
Bucaramanga, Santander               12.9     0.112069      0.033613   
Ibagué, Tolima                        7.0    -0.292929     -0.207792   
Cali, Valle del Cauca                 3.1    -0.162162     -0.306122   

                            rot_tot_vis  
Location                                 
Medellín, Antioquia           -0.326316  
Barranquilla, Atlántico       -0.208955  
Bogotá, D.C., Bogotá, D.C.     0.266667  
Cartagena, Bolívar             0.025974  
Manizales, Caldas             -0.230769  
Montería, Córdoba              0.000000  
Santa Marta, Magdalena         0.320000  
Villavicencio, Meta           -0.407080  
Cúcuta, Norte de Santander    -0.378049  
Armenia, Quindío              -0.311111  
Pereira, Risaralda            -0.513889  
Bucaramanga, Santander 

In [ ]:
stat_aov=df_aov.describe()
stat_aov

Unit Var.  rot2020 vis  rot2020 no-vis  rot2020 total  rot2021 vis  \
count  14.000000    14.000000        14.00000      14.000000    14.000000   
mean   -0.132286     6.742857        19.00000      10.550000     5.464286   
std     0.199976     2.875016         5.29252       3.428108     2.023176   
min    -0.407000     2.200000        11.10000       3.700000     2.000000   
25%    -0.281750     4.525000        14.87500       9.175000     3.850000   
50%    -0.126000     7.450000        18.45000      10.800000     5.750000   
75%    -0.022250     8.800000        23.80000      12.750000     6.475000   
max     0.309000    11.300000        27.20000      15.600000     9.600000   

       rot2021 no-vis  rot2021 total  rot_tot_var  rot_tot_nvis  rot_tot_vis  
count       14.000000      14.000000    14.000000     14.000000    14.000000  
mean        13.064286       7.985714    -0.226224     -0.298706    -0.111986  
std          5.409906       3.173898     0.199399      0.206518     0.302829  
min          8.700000       3.100000    -0.428571     -0.558824    -0.513889  
25%         10.500000       6.450000    -0.381081     -0.478388    -0.322515  
50%         11.000000       7.250000    -0.301465     -0.296504    -0.216978  
75%         12.500000       8.675000    -0.115541     -0.220985     0.019481  
max         26.500000      15.600000     0.158730      0.063063     0.511628

#### Defining groups of data for **annual offer variation** at steps of 25% each

In [ ]:
# Unit housing offer variation
var025=stat_aov.iloc[4,0]
var050=stat_aov.iloc[5,0]
var075=stat_aov.iloc[6,0]
var100=stat_aov.iloc[7,0]
aov = [var025, var050, var075, var100]
print(aov)

[-0.28175, -0.126, -0.02225, 0.309]


In [ ]:
# total inventory rotation variation
var025=stat_aov.iloc[4,7]
var050=stat_aov.iloc[5,7]
var075=stat_aov.iloc[6,7]
var100=stat_aov.iloc[7,7]
arv_t = [var025, var050, var075, var100]
print(arv_t)

[-0.38108100620567376, -0.30146464646464644, -0.1155405405405405, 0.15873015873015872]


In [ ]:
# no vis inventory rotation variation
var025=stat_aov.iloc[4,8]
var050=stat_aov.iloc[5,8]
var075=stat_aov.iloc[6,8]
var100=stat_aov.iloc[7,8]
arv_nvis = [var025, var050, var075, var100]
print(arv_nvis)

[-0.4783882783882784, -0.29650384744061564, -0.22098500091457843, 0.06306306306306315]


In [ ]:
# vis inventory rotation variation
var025=stat_aov.iloc[4,9]
var050=stat_aov.iloc[5,9]
var075=stat_aov.iloc[6,9]
var100=stat_aov.iloc[7,9]
arv_vis = [var025, var050, var075, var100]
print(arv_vis)

[-0.3225146198830409, -0.21697761194029852, 0.019480519480519497, 0.5116279069767442]


Consolidate one table with annual offer variation rates

In [ ]:
frames = [df_aov, df_census]
df_aov = pd.concat(frames, axis=1, join='inner')
df_aov

Unit Var.  rot2020 vis  rot2020 no-vis  \
Location                                                             
Medellín, Antioquia            -0.248          9.5            17.4   
Barranquilla, Atlántico        -0.022          6.7            23.8   
Bogotá, D.C., Bogotá, D.C.      0.309          3.0            14.2   
Cartagena, Bolívar             -0.074          7.7            25.2   
Manizales, Caldas              -0.334          5.2            21.3   
Montería, Córdoba              -0.178          9.6            27.2   
Santa Marta, Magdalena         -0.023          2.5            11.1   
Villavicencio, Meta            -0.407         11.3            15.7   
Cúcuta, Norte de Santander     -0.354          8.2            24.5   
Armenia, Quindío               -0.283          9.0            19.5   
Pereira, Risaralda             -0.278          7.2            12.2   
Bucaramanga, Santander          0.018          4.3            23.8   
Ibagué, Tolima                 -0.057          8.0            15.4   
Cali, Valle del Cauca           0.079          2.2            14.7   

                            rot2020 total  rot2021 vis  rot2021 no-vis  \
Location                                                                 
Medellín, Antioquia                  14.1          6.4            10.6   
Barranquilla, Atlántico               9.7          5.3            10.5   
Bogotá, D.C., Bogotá, D.C.            6.0          3.8            10.5   
Cartagena, Bolívar                   12.6          7.9            12.6   
Manizales, Caldas                    10.0          4.0            10.1   
Montería, Córdoba                    15.6          9.6            26.5   
Santa Marta, Magdalena                6.3          3.3            11.8   
Villavicencio, Meta                  12.8          6.7            11.4   
Cúcuta, Norte de Santander           12.6          5.1            12.6   
Armenia, Quindío                     13.8          6.2            10.6   
Pereira, Risaralda                    9.0          3.5             8.7   
Bucaramanga, Santander               11.6          6.5            24.6   
Ibagué, Tolima                        9.9          6.2            12.2   
Cali, Valle del Cauca                 3.7          2.0            10.2   

                            rot2021 total  rot_tot_var  rot_tot_nvis  \
Location                                                               
Medellín, Antioquia                   8.8    -0.375887     -0.390805   
Barranquilla, Atlántico               6.3    -0.350515     -0.558824   
Bogotá, D.C., Bogotá, D.C.            5.4    -0.100000     -0.260563   
Cartagena, Bolívar                    9.9    -0.214286     -0.500000   
Manizales, Caldas                     6.9    -0.310000     -0.525822   
Montería, Córdoba                    15.6     0.000000     -0.025735   
Santa Marta, Magdalena                7.3     0.158730      0.063063   
Villavicencio, Meta                   7.9    -0.382812     -0.273885   
Cúcuta, Norte de Santander            7.2    -0.428571     -0.485714   
Armenia, Quindío                      8.3    -0.398551     -0.456410   
Pereira, Risaralda                    5.2    -0.422222     -0.286885   
Bucaramanga, Santander               12.9     0.112069      0.033613   
Ibagué, Tolima                        7.0    -0.292929     -0.207792   
Cali, Valle del Cauca                 3.1    -0.162162     -0.306122   

                            rot_tot_vis   latitude  longitude  
Location                                                       
Medellín, Antioquia           -0.326316   6.244338 -75.573553  
Barranquilla, Atlántico       -0.208955  10.979967 -74.801309  
Bogotá, D.C., Bogotá, D.C.     0.266667   4.672662 -74.058174  
Cartagena, Bolívar             0.025974  10.419584 -75.527122  
Manizales, Caldas             -0.230769   5.066891 -75.506666  
Montería, Córdoba              0.000000   8.604605 -75.978320  
Santa Marta, Magdalena         0.320000  11.242229 -74.20

#### Creating folium map for total inventory rotation variation

In [ ]:
# create map of iccv annual variation using latitude and longitude values
map = folium.Map(location=[latitude, longitude], zoom_start=5)

# add markers "Municipalities" to map
for label, lat, lng, var in zip(df_aov.index, df_aov['latitude'], df_aov['longitude'], df_aov['rot_tot_var']):
    label = '{}, {:.2f}'.format(label, var) 
    label = folium.Popup(label, parse_html=True)
    
    if var<=arv_t[0]:
        color='red'
        radius=6
        fill=False
    elif var<=arv_t[1]:
        color='grey'
        radius=6
        fill=False        
    elif var<=arv_t[2]:
        color='orange'
        radius=6
        fill=False        
    elif var<=arv_t[3]:
        color='cyan'
        radius=6
        fill=False        
    else: 
        color='yellow'    
    
    folium.CircleMarker(
        [lat, lng],
        radius=radius,
        popup=label,
        color=color,
        fill=fill,
        fill_color=color,
        fill_opacity=0.7,
        parse_html=False).add_to(map)

map

#### Creating folium map for VIS inventory rotation variation

In [ ]:
# create map of iccv annual variation using latitude and longitude values
map = folium.Map(location=[latitude, longitude], zoom_start=5)

# add markers "Municipalities" to map
for label, lat, lng, var in zip(df_aov.index, df_aov['latitude'], df_aov['longitude'], df_aov['rot_tot_vis']):
    label = '{}, {:.2f}'.format(label, var) 
    label = folium.Popup(label, parse_html=True)
    
    if var<=arv_vis[0]:
        color='red'
        radius=6
        fill=False
    elif var<=arv_vis[1]:
        color='grey'
        radius=6
        fill=False        
    elif var<=arv_vis[2]:
        color='orange'
        radius=6
        fill=False        
    elif var<=arv_vis[3]:
        color='cyan'
        radius=6
        fill=False        
    else: 
        color='yellow'    
    
    folium.CircleMarker(
        [lat, lng],
        radius=radius,
        popup=label,
        color=color,
        fill=fill,
        fill_color=color,
        fill_opacity=0.7,
        parse_html=False).add_to(map)

map

#### Creating folium map for NO-VIS inventory rotation variation

In [ ]:
# create map of iccv annual variation using latitude and longitude values
map = folium.Map(location=[latitude, longitude], zoom_start=5)

# add markers "Municipalities" to map
for label, lat, lng, var in zip(df_aov.index, df_aov['latitude'], df_aov['longitude'], df_aov['rot_tot_nvis']):
    label = '{}, {:.2f}'.format(label, var) 
    label = folium.Popup(label, parse_html=True)
    
    if var<=arv_nvis[0]:
        color='red'
        radius=6
        fill=False
    elif var<=arv_nvis[1]:
        color='grey'
        radius=6
        fill=False        
    elif var<=arv_nvis[2]:
        color='orange'
        radius=6
        fill=False        
    elif var<=arv_nvis[3]:
        color='cyan'
        radius=6
        fill=False        
    else: 
        color='yellow'    
    
    folium.CircleMarker(
        [lat, lng],
        radius=radius,
        popup=label,
        color=color,
        fill=fill,
        fill_color=color,
        fill_opacity=0.7,
        parse_html=False).add_to(map)

map

On a positive note, a considerable decrease in general inventory turnover stands out, more accentuated in the non-VIS segment with a reduction below (-47.8%); the cities that make up the coffee region and Medellín (the project's region of interest) are in the first two percentiles. Similarly stands out, the considerable decrease in Manizales in the NO-VIS segment with (-52.58%).

---

### 4. Region of Interest

**Region of Interest analysis**: After conclusions national scope analysis, an analysis of a Region of Interest is performed to get further insight of what sort of project start to plan.  This region is chosen based on its proximity and cultual and economical influence to Supía.
- Región of interest
> - Supía
> - Riosucio
> - Marmato
> - Manizales
> - Pereira
> - Medellín

sociodemograohics georeferenced analysis.
#### Download and Explore Dataset Real-State Market

Use geopy library to update the latitude and longitude values to Supia, Caldas.

In [ ]:
address = 'Supia, Caldas'

# Geolocation is a simple and clever application which uses google maps api.
geolocator = Nominatim(user_agent="Explorar")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude

print('The geograpical coordinate of Supia are {}, {}.'.format(latitude, longitude))
print(location.raw)

The geograpical coordinate of Supia are 5.4533321, -75.651965.
{'place_id': 258506207, 'licence': 'Data © OpenStreetMap contributors, ODbL 1.0. https://osm.org/copyright', 'osm_type': 'relation', 'osm_id': 408355, 'boundingbox': ['5.3737678', '5.5381879', '-75.7063299', '-75.5846063'], 'lat': '5.4533321', 'lon': '-75.651965', 'display_name': 'Supía, Alto Occidente, Caldas, Región Andina, Colombia', 'class': 'boundary', 'type': 'administrative', 'importance': 0.45248064634289364, 'icon': 'https://nominatim.openstreetmap.org/ui/mapicons//poi_boundary_administrative.p.20.png'}


#### Data preparation

In [ ]:
ri= df_aov[['Unit Var.','rot_tot_var']]
frames = [df_asv, ri]
ri = pd.concat(frames, axis=1, join='inner')
ri

Total Unit Var.  VIS Var.  No-VIS Var.   latitude  \
Location                                                                        
Medellín, Antioquia                    0.08      0.07         0.10   6.244338   
Barranquilla, Atlántico                0.20      0.19         0.25  10.979967   
Bogotá, D.C., Bogotá, D.C.             0.12      0.22        -0.13   4.672662   
Cartagena, Bolívar                    -0.16     -0.23         0.02  10.419584   
Manizales, Caldas                      0.12      0.07         0.17   5.066891   
Montería, Córdoba                     -0.14     -0.17        -0.09   8.604605   
Santa Marta, Magdalena                 0.13      0.70        -0.22  11.242229   
Villavicencio, Meta                    0.03     -0.04         0.19   4.131511   
Cúcuta, Norte de Santander            -0.01     -0.12         0.28   7.897146   
Armenia, Quindío                       0.02     -0.07         0.20   4.536307   
Pereira, Risaralda                     0.07      0.11         0.00   4.814261   
Bucaramanga, Santander                -0.01      0.01        -0.03   7.111461   
Ibagué, Tolima                         0.09      0.14        -0.07   4.444660   
Cali, Valle del Cauca                  0.32      0.32         0.30   3.451792   

                            longitude  Unit Var.  rot_tot_var  
Location                                                       
Medellín, Antioquia        -75.573553     -0.248    -0.375887  
Barranquilla, Atlántico    -74.801309     -0.022    -0.350515  
Bogotá, D.C., Bogotá, D.C. -74.058174      0.309    -0.100000  
Cartagena, Bolívar         -75.527122     -0.074    -0.214286  
Manizales, Caldas          -75.506666     -0.334    -0.310000  
Montería, Córdoba          -75.978320     -0.178     0.000000  
Santa Marta, Magdalena     -74.205561     -0.023     0.158730  
Villavicencio, Meta        -73.620667     -0.407    -0.382812  
Cúcuta, Norte de Santander -72.508039     -0.354    -0.428571  
Armenia, Quindío           -75.672375     -0.283    -0.398551  
Pereira, Risaralda         -75.694678     -0.278    -0.422222  
Bucaramanga, Santander     -73.117287      0.018     0.112069  
Ibagué, Tolima             -75.243001     -0.057    -0.292929  
Cali, Valle del Cauca      -76.532494      0.079    -0.162162

In [ ]:
ri=ri.rename(columns={'Total Unit Var.':'Sales', 'Unit Var.':'Offer'})
ri

Sales  VIS Var.  No-VIS Var.   latitude  \
Location                                                              
Medellín, Antioquia          0.08      0.07         0.10   6.244338   
Barranquilla, Atlántico      0.20      0.19         0.25  10.979967   
Bogotá, D.C., Bogotá, D.C.   0.12      0.22        -0.13   4.672662   
Cartagena, Bolívar          -0.16     -0.23         0.02  10.419584   
Manizales, Caldas            0.12      0.07         0.17   5.066891   
Montería, Córdoba           -0.14     -0.17        -0.09   8.604605   
Santa Marta, Magdalena       0.13      0.70        -0.22  11.242229   
Villavicencio, Meta          0.03     -0.04         0.19   4.131511   
Cúcuta, Norte de Santander  -0.01     -0.12         0.28   7.897146   
Armenia, Quindío             0.02     -0.07         0.20   4.536307   
Pereira, Risaralda           0.07      0.11         0.00   4.814261   
Bucaramanga, Santander      -0.01      0.01        -0.03   7.111461   
Ibagué, Tolima               0.09      0.14        -0.07   4.444660   
Cali, Valle del Cauca        0.32      0.32         0.30   3.451792   

                            longitude  Offer  rot_tot_var  
Location                                                   
Medellín, Antioquia        -75.573553 -0.248    -0.375887  
Barranquilla, Atlántico    -74.801309 -0.022    -0.350515  
Bogotá, D.C., Bogotá, D.C. -74.058174  0.309    -0.100000  
Cartagena, Bolívar         -75.527122 -0.074    -0.214286  
Manizales, Caldas          -75.506666 -0.334    -0.310000  
Montería, Córdoba          -75.978320 -0.178     0.000000  
Santa Marta, Magdalena     -74.205561 -0.023     0.158730  
Villavicencio, Meta        -73.620667 -0.407    -0.382812  
Cúcuta, Norte de Santander -72.508039 -0.354    -0.428571  
Armenia, Quindío           -75.672375 -0.283    -0.398551  
Pereira, Risaralda         -75.694678 -0.278    -0.422222  
Bucaramanga, Santander     -73.117287  0.018     0.112069  
Ibagué, Tolima             -75.243001 -0.057    -0.292929  
Cali, Valle del Cauca      -76.532494  0.079    -0.162162

In [ ]:
#Dropping columns not needed.
ri.drop(['VIS Var.', 'No-VIS Var.'], axis=1, inplace=True)
ri

Sales   latitude  longitude  Offer  rot_tot_var
Location                                                                   
Medellín, Antioquia          0.08   6.244338 -75.573553 -0.248    -0.375887
Barranquilla, Atlántico      0.20  10.979967 -74.801309 -0.022    -0.350515
Bogotá, D.C., Bogotá, D.C.   0.12   4.672662 -74.058174  0.309    -0.100000
Cartagena, Bolívar          -0.16  10.419584 -75.527122 -0.074    -0.214286
Manizales, Caldas            0.12   5.066891 -75.506666 -0.334    -0.310000
Montería, Córdoba           -0.14   8.604605 -75.978320 -0.178     0.000000
Santa Marta, Magdalena       0.13  11.242229 -74.205561 -0.023     0.158730
Villavicencio, Meta          0.03   4.131511 -73.620667 -0.407    -0.382812
Cúcuta, Norte de Santander  -0.01   7.897146 -72.508039 -0.354    -0.428571
Armenia, Quindío             0.02   4.536307 -75.672375 -0.283    -0.398551
Pereira, Risaralda           0.07   4.814261 -75.694678 -0.278    -0.422222
Bucaramanga, Santander      -0.01   7.111461 -73.117287  0.018     0.112069
Ibagué, Tolima               0.09   4.444660 -75.243001 -0.057    -0.292929
Cali, Valle del Cauca        0.32   3.451792 -76.532494  0.079    -0.162162

In [ ]:
#Reordering columns
ri=ri[['latitude','longitude','Sales','Offer','rot_tot_var']]
ri

latitude  longitude  Sales  Offer  rot_tot_var
Location                                                                   
Medellín, Antioquia          6.244338 -75.573553   0.08 -0.248    -0.375887
Barranquilla, Atlántico     10.979967 -74.801309   0.20 -0.022    -0.350515
Bogotá, D.C., Bogotá, D.C.   4.672662 -74.058174   0.12  0.309    -0.100000
Cartagena, Bolívar          10.419584 -75.527122  -0.16 -0.074    -0.214286
Manizales, Caldas            5.066891 -75.506666   0.12 -0.334    -0.310000
Montería, Córdoba            8.604605 -75.978320  -0.14 -0.178     0.000000
Santa Marta, Magdalena      11.242229 -74.205561   0.13 -0.023     0.158730
Villavicencio, Meta          4.131511 -73.620667   0.03 -0.407    -0.382812
Cúcuta, Norte de Santander   7.897146 -72.508039  -0.01 -0.354    -0.428571
Armenia, Quindío             4.536307 -75.672375   0.02 -0.283    -0.398551
Pereira, Risaralda           4.814261 -75.694678   0.07 -0.278    -0.422222
Bucaramanga, Santander       7.111461 -73.117287  -0.01  0.018     0.112069
Ibagué, Tolima               4.444660 -75.243001   0.09 -0.057    -0.292929
Cali, Valle del Cauca        3.451792 -76.532494   0.32  0.079    -0.162162

In [ ]:
# Selecting cities that are part of the region of interest
ri=pd.DataFrame(ri, index=['Medellín, Antioquia','Manizales, Caldas','Pereira, Risaralda'])
ri

latitude  longitude  Sales  Offer  rot_tot_var
Medellín, Antioquia  6.244338 -75.573553   0.08 -0.248    -0.375887
Manizales, Caldas    5.066891 -75.506666   0.12 -0.334    -0.310000
Pereira, Risaralda   4.814261 -75.694678   0.07 -0.278    -0.422222

#### Conclusion

Manizales city present a greater opportunity scenario for housing project, in comparisson with the other cities of the región of interes, it presents the highest sales variation, the lowest offer variation, with a negative variation in the inventory rotation index, threfore higher sales speed.

#### Evaluation of socio demographics in region of interes

In [ ]:
ri_mun=census
if(ri_mun.index.name != 'Location'):
    ri_mun = ri_mun.set_index('Location')


ri_mun=pd.DataFrame(ri_mun, index=['Supía, Caldas','Riosucio, Caldas','Marmato, Caldas','Medellín, Antioquia','Manizales, Caldas','Pereira, Risaralda'] )

ri_mun

Department-2018 Municipality-2018  Total 2018  \
Supía, Caldas                Caldas             Supía       28642   
Riosucio, Caldas             Caldas          Riosucio       50775   
Marmato, Caldas              Caldas           Marmato        8888   
Medellín, Antioquia       Antioquia          Medellín     2427129   
Manizales, Caldas            Caldas         Manizales      434403   
Pereira, Risaralda        Risaralda           Pereira      467269   

                     Housing units 2018  Households 2018  People 2018  \
Supía, Caldas                      9997             8379        26571   
Riosucio, Caldas                  16970            14481        48329   
Marmato, Caldas                    3265             2682         8485   
Medellín, Antioquia              892151           815493      2372330   
Manizales, Caldas                158396           136806       400436   
Pereira, Risaralda               173459           138945       409670   

                     Total 2005  Households 2005   var_pop  var_households  \
Supía, Caldas             24072           6578.0  0.013461        0.018790   
Riosucio, Caldas          35843           9633.0  0.027151        0.031854   
Marmato, Caldas            8175           2023.0  0.006453        0.021928   
Medellín, Antioquia     2219861         605192.0  0.006890        0.023207   
Manizales, Caldas        368433         102773.0  0.012751        0.022247   
Pereira, Risaralda       428397         118529.0  0.006704        0.012300   

                     household/housing ratio  \
Supía, Caldas                       0.838151   
Riosucio, Caldas                    0.853329   
Marmato, Caldas                     0.821440   
Medellín, Antioquia                 0.914075   
Manizales, Caldas                   0.863696   
Pereira, Risaralda                  0.801025   

                                                              location  \
Supía, Caldas        (Supía, Alto Occidente, Caldas, Región Andina,...   
Riosucio, Caldas     (Riosucio, Alto Occidente, Caldas, Región Andi...   
Marmato, Caldas      (Marmato, Alto Occidente, Caldas, Región Andin...   
Medellín, Antioquia  (Medellín, Valle de Aburrá, Antioquia, Región ...   
Manizales, Caldas    (Manizales, Centrosur, Caldas, Región Andina, ...   
Pereira, Risaralda   (Pereira, Centro, Perimetro Urbano Pereira, Pe...   

                                             point  latitude  longitude  \
Supía, Caldas         (5.4533321, -75.651965, 0.0)  5.453332 -75.651965   
Riosucio, Caldas     (5.4209549, -75.7030623, 0.0)  5.420955 -75.703062   
Marmato, Caldas      (5.4746415, -75.5988438, 0.0)  5.474641 -75.598844   
Medellín, Antioquia   (6.2443382, -75.573553, 0.0)  6.244338 -75.573553   
Manizales, Caldas    (5.0668907, -75.5066661, 0.0)  5.066891 -75.506666   
Pereira, Risaralda   (4.8142613, -75.6946776, 0.0)  4.814261 -75.694678   

                     altitude  
Supía, Caldas             0.0  
Riosucio, Caldas          0.0  
Marmato, Caldas           0.0  
Medellín, Antioquia       0.0  
Manizales, Caldas         0.0  
Pereira, Risaralda        0.0

In [ ]:
# Selecting information needs
ri_mun=ri_mun[['latitude','longitude','var_pop','var_households','household/housing ratio']]
ri_mun

latitude  longitude   var_pop  var_households  \
Supía, Caldas        5.453332 -75.651965  0.013461        0.018790   
Riosucio, Caldas     5.420955 -75.703062  0.027151        0.031854   
Marmato, Caldas      5.474641 -75.598844  0.006453        0.021928   
Medellín, Antioquia  6.244338 -75.573553  0.006890        0.023207   
Manizales, Caldas    5.066891 -75.506666  0.012751        0.022247   
Pereira, Risaralda   4.814261 -75.694678  0.006704        0.012300   

                     household/housing ratio  
Supía, Caldas                       0.838151  
Riosucio, Caldas                    0.853329  
Marmato, Caldas                     0.821440  
Medellín, Antioquia                 0.914075  
Manizales, Caldas                   0.863696  
Pereira, Risaralda                  0.801025

#### Creating folium map for  **Region of interes population annual variation map**

In [ ]:
# create map of iccv annual variation using latitude and longitude values
map = folium.Map(location=[latitude, longitude], zoom_start=9)

# add markers "Municipalities" to map
for label, lat, lng, var in zip(ri_mun.index, ri_mun['latitude'], ri_mun['longitude'], ri_mun['var_pop']):
    label = '{}, {:.2f}'.format(label, var) 
    label = folium.Popup(label, parse_html=True)
    
    if var<=0:
        color='red'
        radius=6
        fill=True
    elif var<=pav[1]:
        color='grey'
        radius=6
        fill=True        
    elif var<=pav[2]:
        color='orange'
        radius=6
        fill=True        
    elif var<=pav[3]:
        color='cyan'
        radius=6
        fill=True        
    else: 
        color='yellow'    
    
    folium.CircleMarker(
        [lat, lng],
        radius=radius,
        popup=label,
        color=color,
        fill=fill,
        fill_color=color,
        fill_opacity=0.7,
        parse_html=False).add_to(map)

map

#### Creating folium map for  **Region of interes households annual variation map**

In [ ]:
# create map of iccv annual variation using latitude and longitude values
map = folium.Map(location=[latitude, longitude], zoom_start=9)

# add markers "Municipalities" to map
for label, lat, lng, var in zip(ri_mun.index, ri_mun['latitude'], ri_mun['longitude'], ri_mun['var_households']):
    label = '{}, {:.2f}'.format(label, var) 
    label = folium.Popup(label, parse_html=True)
    
    if var<=0:
        color='red'
        radius=6
        fill=True
    elif var<=hav[1]:
        color='grey'
        radius=6
        fill=True        
    elif var<=hav[2]:
        color='orange'
        radius=6
        fill=True        
    elif var<=hav[3]:
        color='cyan'
        radius=6
        fill=True        
    else: 
        color='yellow'    
    
    folium.CircleMarker(
        [lat, lng],
        radius=radius,
        popup=label,
        color=color,
        fill=fill,
        fill_color=color,
        fill_opacity=0.7,
        parse_html=False).add_to(map)

map

#### Creating folium map for  **Region of interes household/housing ratio map**

In [ ]:
# create map of iccv annual variation using latitude and longitude values
map = folium.Map(location=[latitude, longitude], zoom_start=9)

# add markers "Municipalities" to map
for label, lat, lng, var in zip(ri_mun.index, ri_mun['latitude'], ri_mun['longitude'], ri_mun['household/housing ratio']):
    label = '{}, {:.2f}'.format(label, var) 
    label = folium.Popup(label, parse_html=True)
    
    if var<=hhr[0]:
        color='red'
        radius=6
        fill=True
    elif var<=hhr[1]:
        color='grey'
        radius=6
        fill=True        
    elif var<=hhr[2]:
        color='orange'
        radius=6
        fill=True        
    elif var<=hhr[3]:
        color='cyan'
        radius=6
        fill=True        
    else: 
        color='yellow'    
    
    folium.CircleMarker(
        [lat, lng],
        radius=radius,
        popup=label,
        color=color,
        fill=fill,
        fill_color=color,
        fill_opacity=0.7,
        parse_html=False).add_to(map)

map

#### Conclusion: region of interes georeferenced analysis

It is evident that the municipality of Marmato has the lowest population variation, in contrast to Riosucio, with the highest in the region of interest. It is highlighted that Supía, located between these two municipalities, presents a population variation similar to the cities of the region. On the other hand, regarding households, Supía, together with Pereira, show the lowest growth, Riosucio the highest, and Marmato stands out at the same percentile as Medellín and Manizales.
In the relationship between homes / housing, the need for housing is evident in the city of Medellín.

---

5. **Places of Interest Analysis**: a real state market will continue by georeferencing places of interest in supía, with its  own set of data, as shown below.  Finally a map evaluation (distance from GPS certified point in land) to different places is performed.

Importing List of Neighbourhoods from CSV file

In [111]:
# Read data from CSV file

import os # Find current working directory
os.listdir(os.getcwd())
df = pd.read_csv('Neighborhood_Supia.csv')

# Input Neighborhood Table
#neighbourhood = {'Neighbourhood':['Libertadores', 'Congo', 'El Progreso', 'Las Palmas', 'Guayabal', 'La Cruz', 'La Plazuela', 'Popular',\
#                     'Renán Barco', 'Villa Carmenza', 'La Estrella', 'Los Álamos', 'Codemas', 'La Moravia', 'La Julia', 'La Vega I',\
#                     'La Vega II', 'Los Colores', 'San Lorenzo', 'Torres de la Vega', 'La Pista']}
#df = pd.DataFrame(neighbourhood)

print('Supias has {} neighborhoods.'.format(len(df['Neighborhood'].unique()),df.shape[0]))
df

Supias has 25 neighborhoods.


Neighborhood              Address
0           Libertadores   CARRERA 7 CALLE 30
1                  Congo  CARRERA 10 CALLE 31
2            El Progreso   CARRERA 8 CALLE 35
3             Las Palmas   CARRERA 8 CALLE 30
4               Guayabal   CARRERA 9 CALLE 28
5                La Cruz   CARRERA 8 CALLE 38
6            La Plazuela   CARRERA 9 CALLE 36
7                Popular   CARRERA 8 CALLE 25
8            Renán Barco   CARRERA 9 CALLE 21
9         Villa Carmenza   CARRERA 9 CALLE 18
10           La Estrella   CARRERA 8 CALLE 19
11   Los Álamos / Alamos  CARRERA 5 CALLE 38B
12               Codemas   CARRERA 9 CALLE 39
13  La Moravia / Morabia   CARRERA 8 CALLE 38
14              La Julia   CARRERA 9 CALLE 15
15             La Vega I                  NaN
16            La Vega II                  NaN
17           Los Colores                  NaN
18           San Lorenzo                  NaN
19     Torres de la Vega                  NaN
20               El Lago  CARRERA 10 CALLE 35
21          Las Galerias   CARRERA 8 CALLE 33
22                Centro   CARRERA 7 CALLE 33
23              Matadero  CARRERA 10 CALLE 34
24              La Pista   CARRERA 6 CALLE 35

In [112]:
#Remove Neighborhoods that are 'Not assigned' address
df_no_na = df[df['Address'].notna()]
df_no_na.shape

(20, 2)

Let's get the geographical coordinates of Neighborhoods of Supia

In [113]:
# Neighborhoods = df['Neighborhood']+', Supia, Caldas' #To improve search

# Conveneint function to delay between geocoding calls
geocode = RateLimiter(geolocator.geocode, min_delay_seconds=1)
geocode = lambda query: geolocator.geocode("%s, Supia, Caldas" % query)

# Create location column
# df['location'] = Neighborhoods.apply(geocode)
df['location'] = df['Neighborhood'].apply(geocode)

# Create longitude, laatitude and altitude from location column (returns tuple)
df['Point'] = df['location'].apply(lambda loc: tuple(loc.point) if loc else None)

#Split point column into latitude, longitude and altitude columns (None Point Filtered out)
#df[['latitude', 'longitude', 'altitude']] = pd.DataFrame(df['Point'].tolist(), index=df.index)

df

Neighborhood              Address  \
0           Libertadores   CARRERA 7 CALLE 30   
1                  Congo  CARRERA 10 CALLE 31   
2            El Progreso   CARRERA 8 CALLE 35   
3             Las Palmas   CARRERA 8 CALLE 30   
4               Guayabal   CARRERA 9 CALLE 28   
5                La Cruz   CARRERA 8 CALLE 38   
6            La Plazuela   CARRERA 9 CALLE 36   
7                Popular   CARRERA 8 CALLE 25   
8            Renán Barco   CARRERA 9 CALLE 21   
9         Villa Carmenza   CARRERA 9 CALLE 18   
10           La Estrella   CARRERA 8 CALLE 19   
11   Los Álamos / Alamos  CARRERA 5 CALLE 38B   
12               Codemas   CARRERA 9 CALLE 39   
13  La Moravia / Morabia   CARRERA 8 CALLE 38   
14              La Julia   CARRERA 9 CALLE 15   
15             La Vega I                  NaN   
16            La Vega II                  NaN   
17           Los Colores                  NaN   
18           San Lorenzo                  NaN   
19     Torres de la Vega                  NaN   
20               El Lago  CARRERA 10 CALLE 35   
21          Las Galerias   CARRERA 8 CALLE 33   
22                Centro   CARRERA 7 CALLE 33   
23              Matadero  CARRERA 10 CALLE 34   
24              La Pista   CARRERA 6 CALLE 35   

                                             location  \
0                                                None   
1                                                None   
2                                                None   
3                                                None   
4   (Supía, Alto Occidente, Caldas, Región Andina,...   
5   (Parque La Cruz, Guamal, Supía, Alto Occidente...   
6                                                None   
7                                                None   
8                                                None   
9                                                None   
10                                               None   
11                                               None   
12                                               None   
13                                               None   
14  (La Julia, Supía, Alto Occidente, Caldas, Regi...   
15  (Club La Vega, Supía, Alto Occidente, Caldas, ...   
16  (Club La Vega, Supía, Alto Occidente, Caldas, ...   
17                                               None   
18  (Parroquia San Lorenzo, Calle 33, Guamal, Supí...   
19                                               None   
20                                               None   
21                                               None   
22  (Centro de Enseñanza Automovilistica Conducald...   
23                                               None   
24                                               None   

                                            Point  
0                                            None  
1                                            None  
2                                            None  
3                                            None  
4                    (5.4533321, -75.651965, 0.0)  
5   (5.4587467499999995, -75.64871896790866, 0.0)  
6                                            None  
7                                            None  
8                                            None  
9                                            None  
10                                           None  
11                                           None  
12                                           None  
13                                           None  
14                  (5.4447772, -75.6383901, 0.0)  
15                  (5.4256278, -75.6389748, 0.0)  
16                  (5.4256278, -75.6389748, 0.0)  
17                                           None  
18           (5.4563313, -75.64958324732268, 0.0)  
19                                           None  
20                                           None  
21                                           None  
22                  (5.4527832, -75.6527645, 0.0)  
23    

#### Conclusion

With Nomatin Geopy service the analysis lacks of precision, therefore geopy GoogleV3 is used for Geocoding purposes in a separate notebook.

In [ ]:
# Neighborhoods = df['Address']+', Supia, Caldas' #To improve search

# Conveneint function to delay between geocoding calls
geocode = RateLimiter(geolocator.geocode, min_delay_seconds=1)
geocode = lambda query: geolocator.geocode("%s, Supia, Caldas" % query)

df['location'] = df['Address'].apply(geocode)
df['Point'] = df['location'].apply(lambda loc: tuple(loc.point) if loc else None)

# Split point column into latitude, longitude and altitude columns
df[['Latitude', 'Longitude', 'Altitude']] = pd.DataFrame(df['Point'].tolist(), index=df.index)

df.head()

In [ ]:
#df.drop('latitude', inplace=True, axis=1)    
#df.drop('longitude', inplace=True, axis=1)    
#df.drop('altitude', inplace=True, axis=1)    
#df
#df[df['Address'].notna()

In [ ]:
df[df['Address'].notna()]

In [ ]:
t = df['Latitude'].unique()
t

In [ ]:
s = df['Longitude'].unique()
s

In [ ]:
df

In [ ]:
location = geolocator.geocode('Cra. 7 & Cl. 30, Supía, Caldas')
print(location.address) # Carrera 7, Guamal, Supía, Alto Occidente, Caldas, Región Andina, Colombia, ...
print((location.latitude, location.longitude)) # (5.4499801, -75.6498134)
#print(location.raw) # {'place_id': 132706014, 'licence': 'Data © OpenStreetMap contributors, ODbL 1.0. https://osm.org/copyright', 'osm_type': 'way', 'osm_id': 177984244, 'boundingbox': ['5.4487551', '5.4508116', '-75.6499489', '-75.6496833'], 'lat': '5.4499801', 'lon': '-75.6498134', 'display_name': 'Carrera 7, Guamal, Supía, Alto Occidente, Caldas, Región Andina, Colombia', 'class': 'highway', 'type': 'trunk', 'importance': 0.41000000000000003}

In [ ]:
from geopy.geocoders import Nominatim
geolocator = Nominatim(user_agent="default_user_agent")
reverse = partial(geolocator.reverse, language="es")

location = geolocator.reverse("5.454505480241893, -75.64992861858522")
print(location.address) # Expreso Supía, Carrera 7, Guamal, Supía, Alto Occidente, Caldas, Región Andina, Colombia
print((location.latitude, location.longitude)) # (5.4547638, -75.6500123)
#print(location.raw) # {'place_id': '654513', 'osm_type': 'node', ...}

### Create Map from Supia

In [ ]:
! pip install folium==0.5.0
import folium # plotting library

In [ ]:
# create map of Supia using latitude and longitude values
map = folium.Map(location=[latitude, longitude], zoom_start=11)

# add markers to map
for lat, lng, label in zip(df['Latitude'], df['Longitude'], df['Neighborhood']):
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map)

map